In [1]:
using POMDPs
using Random # for AbstractRNG
using POMDPModelTools
using Pkg
Pkg.add("JSON")

  Updating registry at `~/.julia/registries/General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 %  Updating registry at `~/.julia/registries/JuliaPOMDP`
  Updating git-repo `https://github.com/JuliaPOMDP/Registry`
 Resolving package versions...
 Installed TranscodingStreams ─ v0.9.1
  Updating `~/.julia/environments/v1.0/Project.toml`
 [no changes]
  Updating `~/.julia/environments/v1.0/Manifest.toml`
  [3bb67fe8] ↑ TranscodingStreams v0.9.0 ⇒ v0.9.1


In [2]:
struct ChainMDP <: MDP{Int, Symbol}
    len::Int
    p_success::Float64
    discount::Float64
    theta::Int
end


In [3]:
function POMDPs.generate_s(p::ChainMDP, s::Int, a::Symbol, rng::AbstractRNG)
    if a == :right
        success = min(s+1, p.len)
        failure = max(s-1, 1)
    else # a == :left
        success = max(s-1, 1)
        failure = min(s+1, p.len)
    end
    if s + 1 == p.len
        return p.len 
    elseif  s == 2
        return 1
    end
    return rand(rng) < p.p_success ? success : failure
end


In [4]:
# theta = 10
function POMDPs.reward(p::ChainMDP, s::Int, a::Symbol)
    if s == 2
        return p.theta
    end
    if s + 1 == p.len
        return -p.theta
    end
    if s == 0 || s == p.len
        return 0
    end
    return -1
end

In [5]:
POMDPs.initialstate_distribution(m::ChainMDP) = Deterministic(4)

In [6]:
function POMDPs.isterminal(p::ChainMDP, s::Int)
    if s == 1
        return true
    end
    if s == p.len
        return true
    end
    return false
end        

In [7]:
using POMDPSimulators
using POMDPPolicies

ChainMDP() = ChainMDP(6+2,1.0,.9, 10)
m = ChainMDP()

# policy that maps every input to a right action
policy = FunctionPolicy(s->:right)

for (s, a, r) in stepthrough(m, policy, "s,a,r", max_steps=10)
    @show s
    @show a
    @show r
    render(m, (s,a,r))
    println()
end


┌ Info: Recompiling stale cache file /Users/efan/.julia/compiled/v1.0/POMDPSimulators/i1HOp.ji for POMDPSimulators [e0d0a172-29c6-5d4e-96d0-f262df5d01fd]
└ @ Base loading.jl:1184


s = 4
a = :right
r = -1

s = 5
a = :right
r = -1

s = 6
a = :right
r = -1

s = 7
a = :right
r = -10



In [8]:
using POMDPSimulators
using POMDPPolicies

ChainMDP() = ChainMDP(6+2,1.0,.9, 10)
m = ChainMDP()

# policy that maps every input to a left action
policy = FunctionPolicy(s->:left)

function POMDPs.initialstate_distribution(m::ChainMDP)
    return Deterministic(4)
end
for (s, a, r) in stepthrough(m, policy, "s,a,r", max_steps=10)
    # @show s
    # @show a
    # @show r
    render(m, (s,a,r))
    println("s,a,r:($s,$a,$r)")
end


s,a,r:(4,left,-1)
s,a,r:(3,left,-1)
s,a,r:(2,left,10)


In [9]:

include("./ChainMDP.jl")
ChainMDP() = PFChainMDP.PChainMDP(6+2,1.0,.9, 10)
m = ChainMDP()

# policy that maps every input to a right action
policy = FunctionPolicy(s->:right)

function POMDPs.initialstate_distribution(m::PFChainMDP.PChainMDP)
    return Deterministic(4)
end
for (s, a, r) in stepthrough(m, policy, "s,a,r", max_steps=10)
    # @show s
    # @show a
    # @show r
    render(m, (s,a,r))
    println("s,a,r:($s,$a,$r)")
end


s,a,r:(4,right,-1)
s,a,r:(5,right,-1)
s,a,r:(6,right,-1)
s,a,r:(7,right,-10)


In [10]:
n_agents = 1
agents = Any[]
mdps = Any[]
n_states = 6
n_actions = 2
epochs = 10
H = 10
actions = [1, 2]
action_map = Dict(1 => :left, :2 => :right)
rev_action_map = Dict(:left => 1, :right => 2)
states = 1:(n_states+2)
# setup agents
Q_tables = []
N_tables = zeros((n_agents, n_states+2, n_actions))
print(N_tables)
policies = []
theta = 10
# policy that maps every input to a right action
for i in 1:n_agents
    push!(Q_tables, Dict{Int32,Float32}())
    push!(policies, s->:right)
    push!(mdps, ChainMDP(n_states+2,.9,.9, theta))
end
# policy = s->:right

function update_Q(Q_table, s, a, r, sp, t)
    alpha=.95
    gamma=.95
    # print("s:$s, a:$a, sp:$sp, r:$r")
    Q_table[s][rev_action_map[a]] +=  alpha * (r + gamma * 
        findmax(Q_table[sp])[1] - Q_table[s][rev_action_map[a]])
    #println(Q_table)
end
function POMDPs.initialstate_distribution(m::ChainMDP)
    return Deterministic(Int64((n_states+2)/2))
end
function run_chain!(;policies, mdps, reward_reveal_condition, true_mdp, update_Q, n_agents, n_states,
                    Q_tables, N_tables, epochs, steps)
    for e in 1:epochs
        agents = []
        for i in 1:n_agents
            m = mdps[i]
            push!(agents, 
                  Iterators.Stateful(stepthrough(m, FunctionPolicy(policies[i]), "s,a,r,sp,t", max_steps=steps)))
        end

        println("epoch: $e")
        done = false
        t = 0
        while ! done
           done = true
            
           for i in 1:n_agents
                if isempty(agents[i])
                    println("agent $i is done")
                    continue
                end
                res = popfirst!(agents[i])
                r = res[:r]
                if reward_reveal_condition(r)
                    for mdp in mpds
                        mdp = true_mdp
                    end
                end
                #println("before update: N_table: $N_tables")
                N_tables[i,res[:s],rev_action_map[res[:a]]] += 1
                #println("after update:  N_table: $N_tables")
                # println("update Q")
                update_Q(Q_tables[i],res...)
                t = res[:t]
                println("t: $t, print agent $i result: $res")
          
           end
           # println("t:$t")
           for i in 1:n_agents
                if ! isempty(agents[i])
                    done = false
                end
            end
        end
    end
end
run_chain!(policies=policies,
           mdps=mdps,  
           true_mdp=mdps[1],
           reward_reveal_condition= r -> false,
           update_Q=update_Q,
           n_agents=n_agents,
           n_states=n_states,
           Q_tables=Q_tables,
           N_tables=N_tables,
           epochs=epochs,
           steps=H)

[0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0]

[0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0]epoch: 1


KeyError: KeyError: key 4 not found

In [11]:
function square(x)
    return x * x
end

vals = Dict(1 => 4, 2 => 5, 3 => 6)
Dict(key=> square(val) for (key, val) in vals)

Dict{Int64,Int64} with 3 entries:
  2 => 25
  3 => 36
  1 => 16

In [12]:
A = [1 2; 3 4; 5 6]
B = A .+ 6
C = B .+ 6
D = hcat([A , B , C])

3×1 Array{Array{Int64,2},2}:
 [1 2; 3 4; 5 6]      
 [7 8; 9 10; 11 12]   
 [13 14; 15 16; 17 18]

In [13]:
D[2,:]

1-element Array{Array{Int64,2},1}:
 [7 8; 9 10; 11 12]

In [14]:
function ucb_pol(Q_tables, N_tables, i, actions, s)
    # return 
    C = 10.0
    if haskey(Q_tables[i], s)
       # println("ucb_pol:s:$s, N_tables:$N_tables")
       ucbs = Dict(key => sqrt(log(sum(N_tables[i][s,:])/N_tables[i][s,key])) 
                for (key,val) in Q_tables[i][s])
       # println("ucb: $(ucbs)")
       val, idx = findmax(Dict(key => Q_tables[i][s][key] + C* sqrt(log(sum(N_tables[i][s,:])/N_tables[i][s,key])) 
                for (key,val) in Q_tables[i][s])) # need to test
       return action_map[idx]
    else
       act = action_map[rand(actions, 1)[1]]
       println("selected random action $act!!!!!!!!!!!!!!!!!!!!!") 
       return act
    end
end




ucb_pol (generic function with 1 method)

In [15]:
function q_lookup_pol(Q_tables, N_tables, i, actions, s)
    # return 
    if haskey(Q_tables[i], s)
       val, idx = findmax(Q_tables[i][s]) # need to test
       return action_map[idx]
    else
       act = action_map[rand(actions, 1)[1]]
       println("selected random action $act!!!!!!!!!!!!!!!!!!!!!") 
       return act
    end
end

q_lookup_pol (generic function with 1 method)

In [16]:
function ran_pol(Q_tables, N_tables, i, actions, s)
    # return 
    act = action_map[rand(actions, 1)[1]]
    return act
end

ran_pol (generic function with 1 method)

In [17]:
curry(f, a) = (xs...) -> f(a, xs...)
curry2(f, a, b) = (xs...) -> f(a, b, xs...)
curry3(f, a, b, c) = (xs...) -> f(a, b, c, xs...)
curry4(f, a, b, c, d) = (xs...) -> f(a, b, c, d, xs...)
curry5(f, a, b, c, d, e) = (xs...) -> f(a, b, c, d, e, xs...)
curry6(f, a, b, c, d, e, g) = (xs...) -> f(a, b, c, d, e, g, xs...)

curry6 (generic function with 1 method)

In [18]:
n_states = 10
curry(f, x) = (xs...) -> f(x, xs...)
Q_tables = []
mdps = Any[]
N_tables = zeros((n_agents, n_states+2, n_actions))
policies = []
epochs = 500
theta = 10
H = 10
# Setup Q table according to MDP

n_agents = 1
agents = Any[]
n_states = 10


10

In [19]:
function POMDPs.reward(p::ChainMDP, s::Int, a::Symbol)
    if s == 2
        return 10
    end
    if s + 1 == p.len
        return -10
    end
    if s == 0 || s == p.len
        return 0
    end
    return -1
end

In [20]:
# UCB




#setup
for i in 1:n_agents
    push!(Q_tables, Dict{Int32, Dict{Int32, Float32}}())
    for state in states
      Q_tables[i][state] = Dict{Int32, Float32}()
      # print(Q_tables[i])
      for action in actions
         Q_tables[i][state][action] = 0 
      end
    end
    N_table = N_tables[i,:,:]
    push!(policies, curry(curry(curry(curry(ucb_pol, Q_tables), N_tables),i), actions))
    push!(mdps, ChainMDP(n_states+2,.9,.9, 10))
end

run_chain!(policies, mdps, theta, update_Q, n_agents,  n_states, Q_tables, N_tables, epochs, H)

MethodError: MethodError: no method matching run_chain!(::Array{Any,1}, ::Array{Any,1}, ::Int64, ::typeof(update_Q), ::Int64, ::Int64, ::Array{Any,1}, ::Array{Float64,3}, ::Int64, ::Int64)

In [21]:

n_agents = 10
Q_tables = [deepcopy(Q_tables[1]) for i in range(1,stop=n_agents)]
policies = [deepcopy(policies[1]) for i in range(1,stop=n_agents)]
mdps = [deepcopy(mdps[1]) for i in range(1,stop=n_agents)]
N_tables = zeros((n_agents, n_states+2, n_actions))
run_chain!(policies, mdps, update_Q, n_agents,  n_states, Q_tables, N_tables, epochs, H)

MethodError: MethodError: no method matching run_chain!(::Array{getfield(Main, Symbol("##32#33")){getfield(Main, Symbol("##32#33")){getfield(Main, Symbol("##32#33")){getfield(Main, Symbol("##32#33")){typeof(ucb_pol),Array{Any,1}},Array{Float64,3}},Int64},Array{Int64,1}},1}, ::Array{ChainMDP,1}, ::typeof(update_Q), ::Int64, ::Int64, ::Array{Dict{Int32,Dict{Int32,Float32}},1}, ::Array{Float64,3}, ::Int64, ::Int64)

In [22]:
# paramter for seed sampling
using Distributions
theta = 10 * sign(rand(Bernoulli(0.5))-.5)
ntheta = - theta
print("theta: $theta, ntheta: $ntheta")
# Thompson sampling
#Should just be seed sampling, but you do it every step

theta: 10.0, ntheta: -10.0

In [23]:

using POMDPs
include("./ChainMDP.jl")
num_states = 10

mdp = PFChainMDP.PChainMDP(num_states+2,.9,.9, 10)
POMDPs.reward(mdp, 1, :left)

-1

In [24]:
function update_Q(Q_table, s, a, r, sp, t, rev_action_map)
    alpha=.95
    gamma=.95
    # print("s:$s, a:$a, sp:$sp, r:$r")
    Q_table[s][rev_action_map[a]] +=  alpha * (r + gamma * 
        findmax(Q_table[sp])[1] - Q_table[s][rev_action_map[a]])
    #println(Q_table)
end

update_Q (generic function with 2 methods)

In [25]:
mdps = [deepcopy(mdp) for i in 1:2]
isequal(mdps[1], mdps[2])

mdp1 = PFChainMDP.PChainMDP(num_states+2,.9,.9, 10)

mdp2 = PFChainMDP.PChainMDP(num_states+2,.9,.9, 10)
mdp1 === mdp2

true

In [59]:

using DataFrames
function get_average_regret(df, num_agents)
    num_states = 150
    R = (num_states ) / 2 
    max_theta_state = 2
    #df2 = groupby(groupby(df, :epoch), :agent)
    # Think best way is to just post process to fix it up.
    # find the last state for each epoch for each agent and then fill it out by appending rows
    dfa = deepcopy(df)
    df2 = by(df, [:run, :epoch, :agent], max_t = [:time] => x -> maximum(x.time))
    for row in eachrow(df2)
        state = df[(df[:run].==row.run).&(df[:epoch].==row.epoch).&(
                df[:agent].==row.agent).&(df[:time].==row.max_t),:].state[1]
        #println(state)
        new_time = row.max_t[1]
        new_state = state[1]
        if state == num_states - 1
            continue
        end
        for i in state:max_theta_state
            #println("$state, $max_theta_state, $i")
            new_time += 1
            new_state -=1
            new_row = DataFrame(run = row.run, epoch = row.epoch, agent= row.agent,
                   time = new_time, state = new_state, reward = (new_state == 2) ? 10 : -1)
            append!(dfa,new_row)
        end
    end

    dfa
    #print(dfa)
    df2 = by(dfa, [:run, :epoch, :agent], Regret = [:state, :reward] =>  x ->   R  - sum( x.reward))
    print(df2)
    # df3 = by(df2, [:agent], AverageRegret = [:Regret ] => mean)
    # df3
    #aggregate(df, :Species, [sum, mean])
    #average regret
    df_agents = unique(df.agent)
    for i in 1:num_agents
        if !(i  in df_agents)
            println("Agent $i not in regret")
            # run   │ epoch │ agent │ Regret
            u_runs = unique(df.run)
            u_epoch = unique(df.epoch)
            for a_run in u_runs
                for a_epoch in u_epoch
                    new_df = DataFrame(run = a_run, epoch = a_epoch, agent = i, Regret = 0.0)
                    append!(df2, new_df)
                end
            end
            
        end
    end
    print(df2)
    mean(df2.Regret)
end

get_average_regret (generic function with 1 method)

In [91]:
# UCB
using Distributions
include("./Agent.jl")
num_agents = 5
agents = Any[]
num_states = 100
num_actions = 2
epochs = 30
H = floor(Int, 3 * num_states / 2)
actions = [1, 2]
action_map = Dict(1 => :left, :2 => :right)
rev_action_map = Dict(:left => 1, :right => 2)
states = 1:(num_states+2)

theta = 10
# Setup Q table according to MDP



#setup
#agmdp = PFChainMDP.PChainMDP(num_states+2,1.0,.9, theta * sign(rand(Bernoulli(0.5))-.5))
(Q_tables, N_tables, policies) = PFAgent.setup_agents(states, num_states, num_agents,
                                                            actions, num_actions, ucb_pol)
true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,.9, theta)

function chain_found_target(r)
   if r == -10 || r == 10
        return true
   end
   return false
end

PFAgent.run_chain!(
           policies=policies,
           found_target=chain_found_target,
           mdps=[deepcopy(true_mdp) for i in 1:num_agents],
           update_Q=update_Q,
           n_agents=num_agents,
           n_states=num_states,
           Q_tables=Q_tables,
           N_tables=N_tables,
           epochs=epochs,
           steps=H,
           rev_action_map=rev_action_map,
           stop_early=false)
print(Q_tables)

setup agents


agent 1 is done
agent 1 is done
agent 2 is done
agent 1 is done
agent 2 is done
agent 3 is done
agent 1 is done
agent 2 is done
agent 3 is done
agent 4 is done
agent 1 is done
agent 1 is done
agent 2 is done
agent 1 is done
agent 2 is done
agent 1 is done
agent 2 is done
agent 3 is done
agent 1 is done
agent 2 is done
agent 3 is done
agent 4 is done
e: 3, t: 1, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 3, t: 2, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 2)
e: 3, t: 1, agent 2, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 3, t: 3, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 3)
e: 3, t: 2, agent 2, result: (s = 53, a = :left, r = -1, sp = 52, t = 2)
e: 3, t: 1, agent 3, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 3, t: 4, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 4)
e: 3, t: 3, agent 2, result: (s = 52, a = :right, r = -1, sp = 53, t = 3)
e: 3, t: 2, agent 3, result: (s = 53, a = :right, r = -1, 

e: 3, t: 26, agent 4, result: (s = 55, a = :right, r = -1, sp = 56, t = 26)
e: 3, t: 25, agent 5, result: (s = 56, a = :right, r = -1, sp = 57, t = 25)
e: 3, t: 30, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 30)
e: 3, t: 29, agent 2, result: (s = 56, a = :right, r = -1, sp = 57, t = 29)
e: 3, t: 28, agent 3, result: (s = 49, a = :right, r = -1, sp = 50, t = 28)
e: 3, t: 27, agent 4, result: (s = 56, a = :right, r = -1, sp = 57, t = 27)
e: 3, t: 26, agent 5, result: (s = 57, a = :right, r = -1, sp = 58, t = 26)
e: 3, t: 31, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 31)
e: 3, t: 30, agent 2, result: (s = 57, a = :left, r = -1, sp = 56, t = 30)
e: 3, t: 29, agent 3, result: (s = 50, a = :right, r = -1, sp = 51, t = 29)
e: 3, t: 28, agent 4, result: (s = 57, a = :left, r = -1, sp = 56, t = 28)
e: 3, t: 27, agent 5, result: (s = 58, a = :left, r = -1, sp = 57, t = 27)
e: 3, t: 32, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 32)
e: 3, t: 31, ag

e: 3, t: 52, agent 5, result: (s = 49, a = :right, r = -1, sp = 50, t = 52)
e: 3, t: 57, agent 1, result: (s = 58, a = :left, r = -1, sp = 57, t = 57)
e: 3, t: 56, agent 2, result: (s = 59, a = :right, r = -1, sp = 60, t = 56)
e: 3, t: 55, agent 3, result: (s = 58, a = :left, r = -1, sp = 57, t = 55)
e: 3, t: 54, agent 4, result: (s = 59, a = :right, r = -1, sp = 60, t = 54)
e: 3, t: 53, agent 5, result: (s = 50, a = :right, r = -1, sp = 51, t = 53)
e: 3, t: 58, agent 1, result: (s = 57, a = :left, r = -1, sp = 56, t = 58)
e: 3, t: 57, agent 2, result: (s = 60, a = :left, r = -1, sp = 59, t = 57)
e: 3, t: 56, agent 3, result: (s = 57, a = :left, r = -1, sp = 56, t = 56)
e: 3, t: 55, agent 4, result: (s = 60, a = :left, r = -1, sp = 59, t = 55)
e: 3, t: 54, agent 5, result: (s = 51, a = :right, r = -1, sp = 52, t = 54)
e: 3, t: 59, agent 1, result: (s = 56, a = :left, r = -1, sp = 55, t = 59)
e: 3, t: 58, agent 2, result: (s = 59, a = :left, r = -1, sp = 58, t = 58)
e: 3, t: 57, agent 3

e: 3, t: 84, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 84)
e: 3, t: 83, agent 2, result: (s = 52, a = :left, r = -1, sp = 51, t = 83)
e: 3, t: 82, agent 3, result: (s = 59, a = :left, r = -1, sp = 58, t = 82)
e: 3, t: 81, agent 4, result: (s = 52, a = :left, r = -1, sp = 51, t = 81)
e: 3, t: 80, agent 5, result: (s = 59, a = :right, r = -1, sp = 60, t = 80)
e: 3, t: 85, agent 1, result: (s = 58, a = :left, r = -1, sp = 57, t = 85)
e: 3, t: 84, agent 2, result: (s = 51, a = :left, r = -1, sp = 50, t = 84)
e: 3, t: 83, agent 3, result: (s = 58, a = :left, r = -1, sp = 57, t = 83)
e: 3, t: 82, agent 4, result: (s = 51, a = :left, r = -1, sp = 50, t = 82)
e: 3, t: 81, agent 5, result: (s = 60, a = :right, r = -1, sp = 61, t = 81)
e: 3, t: 86, agent 1, result: (s = 57, a = :left, r = -1, sp = 56, t = 86)
e: 3, t: 85, agent 2, result: (s = 50, a = :left, r = -1, sp = 49, t = 85)
e: 3, t: 84, agent 3, result: (s = 57, a = :left, r = -1, sp = 56, t = 84)
e: 3, t: 83, agent 4, r

...

e: 27, t: 65, agent 1, result: (s = 36, a = :left, r = -1, sp = 35, t = 65)
e: 27, t: 64, agent 2, result: (s = 49, a = :left, r = -1, sp = 48, t = 64)
e: 27, t: 63, agent 3, result: (s = 82, a = :right, r = -1, sp = 83, t = 63)
e: 27, t: 62, agent 4, result: (s = 51, a = :left, r = -1, sp = 50, t = 62)
e: 27, t: 61, agent 5, result: (s = 50, a = :left, r = -1, sp = 49, t = 61)
e: 27, t: 66, agent 1, result: (s = 35, a = :left, r = -1, sp = 34, t = 66)
e: 27, t: 65, agent 2, result: (s = 48, a = :left, r = -1, sp = 47, t = 65)
e: 27, t: 64, agent 3, result: (s = 83, a = :left, r = -1, sp = 82, t = 64)
e: 27, t: 63, agent 4, result: (s = 50, a = :right, r = -1, sp = 51, t = 63)
e: 27, t: 62, agent 5, result: (s = 49, a = :left, r = -1, sp = 48, t = 62)
e: 27, t: 67, agent 1, result: (s = 34, a = :left, r = -1, sp = 33, t = 67)
e: 27, t: 66, agent 2, result: (s = 47, a = :left, r = -1, sp = 46, t = 66)
e: 27, t: 65, agent 3, result: (s = 82, a = :left, r = -1, sp = 81, t = 65)
e: 27, t: 

e: 27, t: 87, agent 5, result: (s = 44, a = :right, r = -1, sp = 45, t = 87)
e: 27, t: 92, agent 1, result: (s = 35, a = :right, r = -1, sp = 36, t = 92)
e: 27, t: 91, agent 2, result: (s = 46, a = :left, r = -1, sp = 45, t = 91)
e: 27, t: 90, agent 3, result: (s = 57, a = :left, r = -1, sp = 56, t = 90)
e: 27, t: 89, agent 4, result: (s = 74, a = :right, r = -1, sp = 75, t = 89)
e: 27, t: 88, agent 5, result: (s = 45, a = :right, r = -1, sp = 46, t = 88)
e: 27, t: 93, agent 1, result: (s = 36, a = :right, r = -1, sp = 37, t = 93)
e: 27, t: 92, agent 2, result: (s = 45, a = :left, r = -1, sp = 44, t = 92)
e: 27, t: 91, agent 3, result: (s = 56, a = :right, r = -1, sp = 57, t = 91)
e: 27, t: 90, agent 4, result: (s = 75, a = :left, r = -1, sp = 74, t = 90)
e: 27, t: 89, agent 5, result: (s = 46, a = :right, r = -1, sp = 47, t = 89)
e: 27, t: 94, agent 1, result: (s = 37, a = :left, r = -1, sp = 36, t = 94)
e: 27, t: 93, agent 2, result: (s = 44, a = :right, r = -1, sp = 45, t = 93)
e: 2

e: 27, t: 117, agent 3, result: (s = 82, a = :right, r = -1, sp = 83, t = 117)
e: 27, t: 116, agent 4, result: (s = 73, a = :right, r = -1, sp = 74, t = 116)
e: 27, t: 115, agent 5, result: (s = 38, a = :left, r = -1, sp = 37, t = 115)
e: 27, t: 120, agent 1, result: (s = 23, a = :left, r = -1, sp = 22, t = 120)
e: 27, t: 119, agent 2, result: (s = 48, a = :left, r = -1, sp = 47, t = 119)
e: 27, t: 118, agent 3, result: (s = 83, a = :right, r = -1, sp = 84, t = 118)
e: 27, t: 117, agent 4, result: (s = 74, a = :right, r = -1, sp = 75, t = 117)
e: 27, t: 116, agent 5, result: (s = 37, a = :left, r = -1, sp = 36, t = 116)
e: 27, t: 121, agent 1, result: (s = 22, a = :left, r = -1, sp = 21, t = 121)
e: 27, t: 120, agent 2, result: (s = 47, a = :left, r = -1, sp = 46, t = 120)
e: 27, t: 119, agent 3, result: (s = 84, a = :left, r = -1, sp = 83, t = 119)
e: 27, t: 118, agent 4, result: (s = 75, a = :right, r = -1, sp = 76, t = 118)
e: 27, t: 117, agent 5, result: (s = 36, a = :left, r = -1,

Excessive output truncated after 524291 bytes.

e: 27, t: 142, agent 4, result: (s = 83, a = :left, r = -1, sp = 82, t = 142)
e: 27, t: 141, agent 5, result: (s = 38, a = :left, r = -1, sp = 37, t = 141)
e: 27, t: 146, agent 1, result: (s = 25, a = :left, r = -1, sp = 24, t = 146)
e: 27, t: 145, agent 2, result: (s = 50, a = :right, r = -1, sp = 51, t = 145)
e: 27, t: 144, agent 3, result: (s = 83, a = :left, r = -1, sp = 82, t = 144)
e: 27, t: 143, agent 4, result: (s = 82, a = :left, r = -1, sp = 81, t = 143)
e: 27, t: 142, agent 5, result: (s = 37, a = :left, r = -1, sp = 36, t = 142)
e: 27, t: 147, agent 1, result: (s = 24, a = :left, r = -1, sp = 23, t = 147)
e: 27, t: 146, agent 2, result: (s = 51, a = :right, r = -1, sp = 52, t = 146)
e: 27, t: 145, agent 3, result: (s = 82, a = :right, r = -1, sp = 83, t = 145)
e: 27, t: 144, agent 4, result: (s = 81, a = :left, r = -1, sp = 80, t = 144)
e: 27, t: 143, agent 5, result: (s = 36, a = :left, r = -1, sp = 35, t = 143)
e: 27, t: 148, agent 1, result: (s = 23, a = :left, r = -1, s

In [92]:

include("./Agent.jl")
# Base setup 

# Solution

# solve mdp in both directions
# Then each agent will pick on of the policies.
# common
num_agents = 1
agents = Any[]
num_states = 100
num_actions = 2
epochs = 100
H = floor(Int, 3 * num_states / 2)
actions = [1, 2]
action_map = Dict(1 => :left, :2 => :right)
rev_action_map = Dict(:left => 1, :right => 2)
states = 1:(num_states+2)


theta = 10


(Q_tables1, N_tables1, policies1) = PFAgent.setup_agents(states, num_states, num_agents,
                                                            actions, num_actions, ucb_pol)

true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,.99, theta)
PFAgent.run_chain!(policies=policies1,
           found_target=chain_found_target,
           mdps=[true_mdp],
           update_Q=update_Q,
           n_agents=num_agents,
           n_states=num_states,
           Q_tables=Q_tables1,
           N_tables=N_tables1,
           epochs=epochs,
           steps=H,
           rev_action_map=rev_action_map,
           stop_early=false)

# theta = -10
using JSON
println("Q1:$(json(Q_tables1,2))")
println("N1:$(json(N_tables1,2))")

true_mdp2 = PFChainMDP.PChainMDP(num_states+2,1.0,.99, -theta)
(Q_tables2, N_tables2, policies2) = PFAgent.setup_agents(states, num_states, num_agents,
                                                            actions, num_actions, ucb_pol)
PFAgent.run_chain!(policies=policies2,
           found_target=chain_found_target,
           mdps=[true_mdp2],
           update_Q=update_Q,
           n_agents=num_agents,
           n_states=num_states,
           Q_tables=Q_tables2,
           N_tables=N_tables2,
           epochs=epochs,
           steps=H,
           rev_action_map=rev_action_map,
           stop_early=false)



println("Q2: $(json(Q_tables2[1],2))")
println("N2: $(json(N_tables2[1],2))")

setup agents


e: 10, t: 1, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 10, t: 2, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 10, t: 3, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 3)
e: 10, t: 4, agent 1, result: (s = 55, a = :right, r = -1, sp = 56, t = 4)
e: 10, t: 5, agent 1, result: (s = 56, a = :right, r = -1, sp = 57, t = 5)
e: 10, t: 6, agent 1, result: (s = 57, a = :right, r = -1, sp = 58, t = 6)
e: 10, t: 7, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 7)
e: 10, t: 8, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 8)
e: 10, t: 9, agent 1, result: (s = 60, a = :right, r = -1, sp = 61, t = 9)
e: 10, t: 10, agent 1, result: (s = 61, a = :right, r = -1, sp = 62, t = 10)
e: 10, t: 11, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 11)
e: 10, t: 12, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 12)
e: 10, t: 13, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 13)
e: 10, t: 14, agen

e: 10, t: 135, agent 1, result: (s = 74, a = :right, r = -1, sp = 75, t = 135)
e: 10, t: 136, agent 1, result: (s = 75, a = :right, r = -1, sp = 76, t = 136)
e: 10, t: 137, agent 1, result: (s = 76, a = :right, r = -1, sp = 77, t = 137)
e: 10, t: 138, agent 1, result: (s = 77, a = :right, r = -1, sp = 78, t = 138)
e: 10, t: 139, agent 1, result: (s = 78, a = :left, r = -1, sp = 77, t = 139)
e: 10, t: 140, agent 1, result: (s = 77, a = :left, r = -1, sp = 76, t = 140)
e: 10, t: 141, agent 1, result: (s = 76, a = :left, r = -1, sp = 75, t = 141)
e: 10, t: 142, agent 1, result: (s = 75, a = :left, r = -1, sp = 74, t = 142)
e: 10, t: 143, agent 1, result: (s = 74, a = :left, r = -1, sp = 73, t = 143)
e: 10, t: 144, agent 1, result: (s = 73, a = :left, r = -1, sp = 72, t = 144)
e: 10, t: 145, agent 1, result: (s = 72, a = :left, r = -1, sp = 71, t = 145)
e: 10, t: 146, agent 1, result: (s = 71, a = :right, r = -1, sp = 72, t = 146)
e: 10, t: 147, agent 1, result: (s = 72, a = :right, r = -1

e: 20, t: 119, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 119)
e: 20, t: 120, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 120)
e: 20, t: 121, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 121)
e: 20, t: 122, agent 1, result: (s = 55, a = :left, r = -1, sp = 54, t = 122)
e: 20, t: 123, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 123)
e: 20, t: 124, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 124)
e: 20, t: 125, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 125)
e: 20, t: 126, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 126)
e: 20, t: 127, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 127)
e: 20, t: 128, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 128)
e: 20, t: 129, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 129)
e: 20, t: 130, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 130)
e: 20, t: 131, agent 1, result: (s = 54, a = :left, r = -

e: 30, t: 103, agent 1, result: (s = 64, a = :left, r = -1, sp = 63, t = 103)
e: 30, t: 104, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 104)
e: 30, t: 105, agent 1, result: (s = 62, a = :left, r = -1, sp = 61, t = 105)
e: 30, t: 106, agent 1, result: (s = 61, a = :left, r = -1, sp = 60, t = 106)
e: 30, t: 107, agent 1, result: (s = 60, a = :left, r = -1, sp = 59, t = 107)
e: 30, t: 108, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 108)
e: 30, t: 109, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 109)
e: 30, t: 110, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 110)
e: 30, t: 111, agent 1, result: (s = 60, a = :left, r = -1, sp = 59, t = 111)
e: 30, t: 112, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 112)
e: 30, t: 113, agent 1, result: (s = 58, a = :left, r = -1, sp = 57, t = 113)
e: 30, t: 114, agent 1, result: (s = 57, a = :left, r = -1, sp = 56, t = 114)
e: 30, t: 115, agent 1, result: (s = 56, a = :left, r = -1, sp

...

e: 60, t: 119, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 119)
e: 60, t: 120, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 120)
e: 60, t: 121, agent 1, result: (s = 62, a = :left, r = -1, sp = 61, t = 121)
e: 60, t: 122, agent 1, result: (s = 61, a = :left, r = -1, sp = 60, t = 122)
e: 60, t: 123, agent 1, result: (s = 60, a = :left, r = -1, sp = 59, t = 123)
e: 60, t: 124, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 124)
e: 60, t: 125, agent 1, result: (s = 58, a = :left, r = -1, sp = 57, t = 125)
e: 60, t: 126, agent 1, result: (s = 57, a = :right, r = -1, sp = 58, t = 126)
e: 60, t: 127, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 127)
e: 60, t: 128, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 128)
e: 60, t: 129, agent 1, result: (s = 60, a = :right, r = -1, sp = 61, t = 129)
e: 60, t: 130, agent 1, result: (s = 61, a = :right, r = -1, sp = 62, t = 130)
e: 60, t: 131, agent 1, result: (s = 62, a = :left, r = -1

e: 70, t: 103, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 103)
e: 70, t: 104, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 104)
e: 70, t: 105, agent 1, result: (s = 48, a = :left, r = -1, sp = 47, t = 105)
e: 70, t: 106, agent 1, result: (s = 47, a = :left, r = -1, sp = 46, t = 106)
e: 70, t: 107, agent 1, result: (s = 46, a = :left, r = -1, sp = 45, t = 107)
e: 70, t: 108, agent 1, result: (s = 45, a = :left, r = -1, sp = 44, t = 108)
e: 70, t: 109, agent 1, result: (s = 44, a = :left, r = -1, sp = 43, t = 109)
e: 70, t: 110, agent 1, result: (s = 43, a = :left, r = -1, sp = 42, t = 110)
e: 70, t: 111, agent 1, result: (s = 42, a = :right, r = -1, sp = 43, t = 111)
e: 70, t: 112, agent 1, result: (s = 43, a = :right, r = -1, sp = 44, t = 112)
e: 70, t: 113, agent 1, result: (s = 44, a = :left, r = -1, sp = 43, t = 113)
e: 70, t: 114, agent 1, result: (s = 43, a = :right, r = -1, sp = 44, t = 114)
e: 70, t: 115, agent 1, result: (s = 44, a = :right, r = -1, 

e: 80, t: 86, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 86)
e: 80, t: 87, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 87)
e: 80, t: 88, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 88)
e: 80, t: 89, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 89)
e: 80, t: 90, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 90)
e: 80, t: 91, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 91)
e: 80, t: 92, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 92)
e: 80, t: 93, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 93)
e: 80, t: 94, agent 1, result: (s = 55, a = :right, r = -1, sp = 56, t = 94)
e: 80, t: 95, agent 1, result: (s = 56, a = :right, r = -1, sp = 57, t = 95)
e: 80, t: 96, agent 1, result: (s = 57, a = :right, r = -1, sp = 58, t = 96)
e: 80, t: 97, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 97)
e: 80, t: 98, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 98)
e

e: 90, t: 135, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 135)
e: 90, t: 136, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 136)
e: 90, t: 137, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 137)
e: 90, t: 138, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 138)
e: 90, t: 139, agent 1, result: (s = 48, a = :left, r = -1, sp = 47, t = 139)
e: 90, t: 140, agent 1, result: (s = 47, a = :right, r = -1, sp = 48, t = 140)
e: 90, t: 141, agent 1, result: (s = 48, a = :right, r = -1, sp = 49, t = 141)
e: 90, t: 142, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 142)
e: 90, t: 143, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 143)
e: 90, t: 144, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 144)
e: 90, t: 145, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 145)
e: 90, t: 146, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 146)
e: 90, t: 147, agent 1, result: (s = 54, a = :right, r = 

e: 100, t: 117, agent 1, result: (s = 32, a = :right, r = -1, sp = 33, t = 117)
e: 100, t: 118, agent 1, result: (s = 33, a = :right, r = -1, sp = 34, t = 118)
e: 100, t: 119, agent 1, result: (s = 34, a = :right, r = -1, sp = 35, t = 119)
e: 100, t: 120, agent 1, result: (s = 35, a = :right, r = -1, sp = 36, t = 120)
e: 100, t: 121, agent 1, result: (s = 36, a = :left, r = -1, sp = 35, t = 121)
e: 100, t: 122, agent 1, result: (s = 35, a = :left, r = -1, sp = 34, t = 122)
e: 100, t: 123, agent 1, result: (s = 34, a = :left, r = -1, sp = 33, t = 123)
e: 100, t: 124, agent 1, result: (s = 33, a = :right, r = -1, sp = 34, t = 124)
e: 100, t: 125, agent 1, result: (s = 34, a = :right, r = -1, sp = 35, t = 125)
e: 100, t: 126, agent 1, result: (s = 35, a = :right, r = -1, sp = 36, t = 126)
e: 100, t: 127, agent 1, result: (s = 36, a = :right, r = -1, sp = 37, t = 127)
e: 100, t: 128, agent 1, result: (s = 37, a = :right, r = -1, sp = 38, t = 128)
e: 100, t: 129, agent 1, result: (s = 38, a

In [93]:
#Now we run with that policy
include("./Agent.jl")
function run_ucb_chain_simulations(nruns, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
    runs = []
    for i in 1:nruns
        agents = Any[]
        num_states = 100
        num_actions = 2
        epochs=1
        ucb_policies = []
        H = floor(Int, 3 * num_states / 2)
        actions = [1, 2]
        action_map = Dict(1 => :left, :2 => :right)
        rev_action_map = Dict(:left => 1, :right => 2)
        states = 1:(num_states+2)
        #print("Before q's")
        true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,.9, 10 * sign(rand(Bernoulli(0.5))-.5))
#         Q_tables_ucb = Dict(1 => Q_tables1[1])
#         N_tables_ucb = Dict(1 => N_tables1[1])
        Q_tables_list = [Q_tables1[1], Q_tables2[1]]
        N_tables_list = [N_tables1[1], N_tables2[1]]
        Q_tables_ucb = Dict(i => Q_tables_list[rand(1:length(Q_tables_list))] for i in 1:num_agents)
        N_tables_ucb = Dict(i => N_tables_list[rand(1:length(N_tables_list))] for i in 1:num_agents)
        #println("Q_T: $Q_tables_thomp")
        #println("N_T: $N_tables_thomp")
        for ag in 1:num_agents
          #push!(ucb_policies, curry(curry(curry(curry(ucb_pol, Q_tables_ucb), N_tables_ucb),1), actions))

          push!(ucb_policies, curry(curry(curry(curry(q_lookup_pol, Q_tables_ucb), N_tables_ucb),1), actions))

        end
        # push!(thomp_policies, curry(curry(curry(curry(thomp_pol_func, Q_tables_thomp), N_tables_thomp),0), actions))
        #println("after policies")
        (Q_tables3, N_tables3, trash) = PFAgent.setup_agents(states, num_states, num_agents,
                                                                    actions, num_actions, ucb_pol)

        mdps = [deepcopy(true_mdp) for ag in 1:num_agents]
        r_history = PFAgent.run_chain!(
                   policies=ucb_policies,
                   found_target=chain_found_target,
                   mdps=mdps,
                   update_Q=update_Q,
                   n_agents=num_agents,
                   n_states=num_states,
                   Q_tables=deepcopy(Q_tables_ucb),
                   N_tables=deepcopy(N_tables_ucb),
                   epochs=epochs,
                   steps=H,
                   rev_action_map=rev_action_map,
                   stop_early=true)

        R = (num_states - 2) / 2
        #println([r for (e,i,t,r) in r_history if i == 1])
        #println([r for (e,i,t,r) in r_history if i == 2])
        for (e, ag, t, st, r)  in r_history
          push!(runs, (i, e, ag, t, st, r)) 
        end
    end
    return runs
end

run_ucb_chain_simulations (generic function with 1 method)

In [102]:
num_agents = 10000
results = run_ucb_chain_simulations(30, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
using CSV
using DataFrames
df_ucb = DataFrame(run = [x[1] for x in results], epoch = [x[2] for x in results], agent=[x[3] for x in results],
               time = [x[4] for x in results], state = [x[5] for x in results], reward = [x[6] for x in results])


setup agents
e: 1, t: 1, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 2, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 2, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 3, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 2, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 3, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 4, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 2, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 3, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 4, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 5, agent 1, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 2, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 3, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 4, result: (s = 51, 

e: 1, t: 13, agent 5, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 6, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 7, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 8, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 9, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 10, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agent 11, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 12, result: (s = 47, a = :left, r = -1, sp = 46, t = 6)
e: 1, t: 5, agent 13, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 14, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 15, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 16, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 17, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 18, agent 1, result: (s = 

e: 1, t: 22, agent 3, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 4, result: (s = 32, a = :left, r = -1, sp = 31, t = 21)
e: 1, t: 20, agent 5, result: (s = 33, a = :left, r = -1, sp = 32, t = 20)
e: 1, t: 19, agent 6, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 7, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 8, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 9, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 10, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 11, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 12, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 13, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 14, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 15, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 1

e: 1, t: 20, agent 10, result: (s = 33, a = :left, r = -1, sp = 32, t = 20)
e: 1, t: 19, agent 11, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 12, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 13, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 14, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 15, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 16, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 17, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 18, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 19, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 20, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 21, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 22, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agen

e: 1, t: 9, agent 25, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 26, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agent 27, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 28, result: (s = 47, a = :left, r = -1, sp = 46, t = 6)
e: 1, t: 5, agent 29, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 30, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 31, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 32, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 33, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 34, agent 1, result: (s = 19, a = :left, r = -1, sp = 18, t = 34)
e: 1, t: 33, agent 2, result: (s = 20, a = :left, r = -1, sp = 19, t = 33)
e: 1, t: 32, agent 3, result: (s = 21, a = :left, r = -1, sp = 20, t = 32)
e: 1, t: 31, agent 4, result: (s = 22, a = :left, r = -1, sp = 21, t = 31)
e: 1, t: 30, agent 5, result: (s =

...

e: 1, t: 22, agent 3, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 4, result: (s = 32, a = :left, r = -1, sp = 31, t = 21)
e: 1, t: 20, agent 5, result: (s = 33, a = :left, r = -1, sp = 32, t = 20)
e: 1, t: 19, agent 6, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 7, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 8, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 9, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 10, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 11, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 12, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 13, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 14, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 15, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 1

e: 1, t: 20, agent 10, result: (s = 33, a = :left, r = -1, sp = 32, t = 20)
e: 1, t: 19, agent 11, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 12, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 13, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 14, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 15, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 16, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 17, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 18, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 19, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 20, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 21, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 22, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agen

Excessive output truncated after 524345 bytes.

e: 1, t: 9, agent 25, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 26, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agent 27, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 28, result: (s = 47, a = :left, r = -1, sp = 46, t = 6)
e: 1, t: 5, agent 29, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 30, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 31, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 32, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 33, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 34, agent 1, result: (s = 19, a = :left, r = -1, sp = 18, t = 34)
e: 1, t: 33, agent 2, result: (s = 20, a = :left, r = -1, sp = 19, t = 33)
e: 1, t: 32, agent 3, result: (s = 21, a = :left, r = -1, sp = 20, t = 32)
e: 1, t: 31, agent 4, result: (s = 22, a = :left, r = -1, sp = 21, t = 31)
e: 1, t: 30, agent 5, result: (s =

38280×6 DataFrame
│ Row   │ run   │ epoch │ agent │ time  │ state │ reward │
│       │ Int64 │ Int64 │ Int64 │ Int64 │ Int64 │ Int64  │
├───────┼───────┼───────┼───────┼───────┼───────┼────────┤
│ 1     │ 1     │ 1     │ 1     │ 1     │ 52    │ -1     │
│ 2     │ 1     │ 1     │ 1     │ 2     │ 51    │ -1     │
│ 3     │ 1     │ 1     │ 2     │ 1     │ 52    │ -1     │
│ 4     │ 1     │ 1     │ 1     │ 3     │ 50    │ -1     │
│ 5     │ 1     │ 1     │ 2     │ 2     │ 51    │ -1     │
│ 6     │ 1     │ 1     │ 3     │ 1     │ 52    │ -1     │
│ 7     │ 1     │ 1     │ 1     │ 4     │ 49    │ -1     │
│ 8     │ 1     │ 1     │ 2     │ 3     │ 50    │ -1     │
│ 9     │ 1     │ 1     │ 3     │ 2     │ 51    │ -1     │
│ 10    │ 1     │ 1     │ 4     │ 1     │ 52    │ -1     │
⋮
│ 38270 │ 30    │ 1     │ 41    │ 10    │ 43    │ -1     │
│ 38271 │ 30    │ 1     │ 42    │ 9     │ 44    │ -1     │
│ 38272 │ 30    │ 1     │ 43    │ 8     │ 45    │ -1     │
│ 38273 │ 30    │ 1     │ 44    │ 7     │ 46    │ -1     │
│ 38274 │ 30    │ 1     │ 45    │ 6     │ 47    │ -1     │
│ 38275 │ 30    │ 1     │ 46    │ 5     │ 48    │ -1     │
│ 38276 │ 30    │ 1     │ 47    │ 4     │ 49    │ -1     │
│ 38277 │ 30    │ 1     │ 48    │ 3     │ 50    │ -1     │
│ 38278 │ 30    │ 1     │ 49    │ 2     │ 51    │ -1     │
│ 38279 │ 30    │ 1     │ 50    │ 1     │ 52    │ -1     │
│ 38280 │ 30    │ 1     │ 1     │ 51    │ 2     │ -10    │

In [103]:

get_average_regret(df_ucb, num_agents)





1500×4 DataFrame
│ Row  │ run   │ epoch │ agent │ Regret  │
│      │ Int64 │ Int64 │ Int64 │ Float64 │
├──────┼───────┼───────┼───────┼─────────┤
│ 1    │ 1     │ 1     │ 1     │ 136.0   │
│ 2    │ 1     │ 1     │ 2     │ 124.0   │
│ 3    │ 1     │ 1     │ 3     │ 123.0   │
│ 4    │ 1     │ 1     │ 4     │ 122.0   │
│ 5    │ 1     │ 1     │ 5     │ 121.0   │
│ 6    │ 1     │ 1     │ 6     │ 120.0   │
│ 7    │ 1     │ 1     │ 7     │ 119.0   │
│ 8    │ 1     │ 1     │ 8     │ 118.0   │
│ 9    │ 1     │ 1     │ 9     │ 117.0   │
│ 10   │ 1     │ 1     │ 10    │ 116.0   │
│ 11   │ 1     │ 1     │ 11    │ 115.0   │
│ 12   │ 1     │ 1     │ 12    │ 114.0   │
│ 13   │ 1     │ 1     │ 13    │ 113.0   │
│ 14   │ 1     │ 1     │ 14    │ 112.0   │
│ 15   │ 1     │ 1     │ 15    │ 111.0   │
│ 16   │ 1     │ 1     │ 16    │ 110.0   │
│ 17   │ 1     │ 1     │ 17    │ 109.0   │
│ 18   │ 1     │ 1     │ 18    │ 108.0   │
│ 19   │ 1     │ 1     │ 19    │ 107.0   │
│ 20   │ 1     │ 1     │ 20    │ 106.

│ 291  │ 6     │ 1     │ 41    │ 85.0    │
│ 292  │ 6     │ 1     │ 42    │ 84.0    │
│ 293  │ 6     │ 1     │ 43    │ 83.0    │
│ 294  │ 6     │ 1     │ 44    │ 82.0    │
│ 295  │ 6     │ 1     │ 45    │ 81.0    │
│ 296  │ 6     │ 1     │ 46    │ 80.0    │
│ 297  │ 6     │ 1     │ 47    │ 79.0    │
│ 298  │ 6     │ 1     │ 48    │ 78.0    │
│ 299  │ 6     │ 1     │ 49    │ 77.0    │
│ 300  │ 6     │ 1     │ 50    │ 76.0    │
│ 301  │ 7     │ 1     │ 1     │ 116.0   │
│ 302  │ 7     │ 1     │ 2     │ 124.0   │
│ 303  │ 7     │ 1     │ 3     │ 123.0   │
│ 304  │ 7     │ 1     │ 4     │ 122.0   │
│ 305  │ 7     │ 1     │ 5     │ 121.0   │
│ 306  │ 7     │ 1     │ 6     │ 120.0   │
│ 307  │ 7     │ 1     │ 7     │ 119.0   │
│ 308  │ 7     │ 1     │ 8     │ 118.0   │
│ 309  │ 7     │ 1     │ 9     │ 117.0   │
│ 310  │ 7     │ 1     │ 10    │ 116.0   │
│ 311  │ 7     │ 1     │ 11    │ 115.0   │
│ 312  │ 7     │ 1     │ 12    │ 114.0   │
│ 313  │ 7     │ 1     │ 13    │ 113.0   │
│ 314  │ 7 

│ 578  │ 12    │ 1     │ 28    │ 98.0    │
│ 579  │ 12    │ 1     │ 29    │ 97.0    │
│ 580  │ 12    │ 1     │ 30    │ 96.0    │
│ 581  │ 12    │ 1     │ 31    │ 95.0    │
│ 582  │ 12    │ 1     │ 32    │ 94.0    │
│ 583  │ 12    │ 1     │ 33    │ 93.0    │
│ 584  │ 12    │ 1     │ 34    │ 92.0    │
│ 585  │ 12    │ 1     │ 35    │ 91.0    │
│ 586  │ 12    │ 1     │ 36    │ 90.0    │
│ 587  │ 12    │ 1     │ 37    │ 89.0    │
│ 588  │ 12    │ 1     │ 38    │ 88.0    │
│ 589  │ 12    │ 1     │ 39    │ 87.0    │
│ 590  │ 12    │ 1     │ 40    │ 86.0    │
│ 591  │ 12    │ 1     │ 41    │ 85.0    │
│ 592  │ 12    │ 1     │ 42    │ 84.0    │
│ 593  │ 12    │ 1     │ 43    │ 83.0    │
│ 594  │ 12    │ 1     │ 44    │ 82.0    │
│ 595  │ 12    │ 1     │ 45    │ 81.0    │
│ 596  │ 12    │ 1     │ 46    │ 80.0    │
│ 597  │ 12    │ 1     │ 47    │ 79.0    │
│ 598  │ 12    │ 1     │ 48    │ 78.0    │
│ 599  │ 12    │ 1     │ 49    │ 77.0    │
│ 600  │ 12    │ 1     │ 50    │ 76.0    │
│ 601  │ 13

│ 879  │ 18    │ 1     │ 29    │ 97.0    │
│ 880  │ 18    │ 1     │ 30    │ 96.0    │
│ 881  │ 18    │ 1     │ 31    │ 95.0    │
│ 882  │ 18    │ 1     │ 32    │ 94.0    │
│ 883  │ 18    │ 1     │ 33    │ 93.0    │
│ 884  │ 18    │ 1     │ 34    │ 92.0    │
│ 885  │ 18    │ 1     │ 35    │ 91.0    │
│ 886  │ 18    │ 1     │ 36    │ 90.0    │
│ 887  │ 18    │ 1     │ 37    │ 89.0    │
│ 888  │ 18    │ 1     │ 38    │ 88.0    │
│ 889  │ 18    │ 1     │ 39    │ 87.0    │
│ 890  │ 18    │ 1     │ 40    │ 86.0    │
│ 891  │ 18    │ 1     │ 41    │ 85.0    │
│ 892  │ 18    │ 1     │ 42    │ 84.0    │
│ 893  │ 18    │ 1     │ 43    │ 83.0    │
│ 894  │ 18    │ 1     │ 44    │ 82.0    │
│ 895  │ 18    │ 1     │ 45    │ 81.0    │
│ 896  │ 18    │ 1     │ 46    │ 80.0    │
│ 897  │ 18    │ 1     │ 47    │ 79.0    │
│ 898  │ 18    │ 1     │ 48    │ 78.0    │
│ 899  │ 18    │ 1     │ 49    │ 77.0    │
│ 900  │ 18    │ 1     │ 50    │ 76.0    │
│ 901  │ 19    │ 1     │ 1     │ 116.0   │
│ 902  │ 19

│ 1177 │ 24    │ 1     │ 27    │ 99.0    │
│ 1178 │ 24    │ 1     │ 28    │ 98.0    │
│ 1179 │ 24    │ 1     │ 29    │ 97.0    │
│ 1180 │ 24    │ 1     │ 30    │ 96.0    │
│ 1181 │ 24    │ 1     │ 31    │ 95.0    │
│ 1182 │ 24    │ 1     │ 32    │ 94.0    │
│ 1183 │ 24    │ 1     │ 33    │ 93.0    │
│ 1184 │ 24    │ 1     │ 34    │ 92.0    │
│ 1185 │ 24    │ 1     │ 35    │ 91.0    │
│ 1186 │ 24    │ 1     │ 36    │ 90.0    │
│ 1187 │ 24    │ 1     │ 37    │ 89.0    │
│ 1188 │ 24    │ 1     │ 38    │ 88.0    │
│ 1189 │ 24    │ 1     │ 39    │ 87.0    │
│ 1190 │ 24    │ 1     │ 40    │ 86.0    │
│ 1191 │ 24    │ 1     │ 41    │ 85.0    │
│ 1192 │ 24    │ 1     │ 42    │ 84.0    │
│ 1193 │ 24    │ 1     │ 43    │ 83.0    │
│ 1194 │ 24    │ 1     │ 44    │ 82.0    │
│ 1195 │ 24    │ 1     │ 45    │ 81.0    │
│ 1196 │ 24    │ 1     │ 46    │ 80.0    │
│ 1197 │ 24    │ 1     │ 47    │ 79.0    │
│ 1198 │ 24    │ 1     │ 48    │ 78.0    │
│ 1199 │ 24    │ 1     │ 49    │ 77.0    │
│ 1200 │ 24

...

│ 2879   │ 29    │ 1     │ 96    │ 0.0     │
│ 2880   │ 30    │ 1     │ 96    │ 0.0     │
│ 2881   │ 1     │ 1     │ 97    │ 0.0     │
│ 2882   │ 2     │ 1     │ 97    │ 0.0     │
│ 2883   │ 3     │ 1     │ 97    │ 0.0     │
│ 2884   │ 4     │ 1     │ 97    │ 0.0     │
│ 2885   │ 5     │ 1     │ 97    │ 0.0     │
│ 2886   │ 6     │ 1     │ 97    │ 0.0     │
│ 2887   │ 7     │ 1     │ 97    │ 0.0     │
│ 2888   │ 8     │ 1     │ 97    │ 0.0     │
│ 2889   │ 9     │ 1     │ 97    │ 0.0     │
│ 2890   │ 10    │ 1     │ 97    │ 0.0     │
│ 2891   │ 11    │ 1     │ 97    │ 0.0     │
│ 2892   │ 12    │ 1     │ 97    │ 0.0     │
│ 2893   │ 13    │ 1     │ 97    │ 0.0     │
│ 2894   │ 14    │ 1     │ 97    │ 0.0     │
│ 2895   │ 15    │ 1     │ 97    │ 0.0     │
│ 2896   │ 16    │ 1     │ 97    │ 0.0     │
│ 2897   │ 17    │ 1     │ 97    │ 0.0     │
│ 2898   │ 18    │ 1     │ 97    │ 0.0     │
│ 2899   │ 19    │ 1     │ 97    │ 0.0     │
│ 2900   │ 20    │ 1     │ 97    │ 0.0     │
│ 2901   │

│ 3148   │ 28    │ 1     │ 105   │ 0.0     │
│ 3149   │ 29    │ 1     │ 105   │ 0.0     │
│ 3150   │ 30    │ 1     │ 105   │ 0.0     │
│ 3151   │ 1     │ 1     │ 106   │ 0.0     │
│ 3152   │ 2     │ 1     │ 106   │ 0.0     │
│ 3153   │ 3     │ 1     │ 106   │ 0.0     │
│ 3154   │ 4     │ 1     │ 106   │ 0.0     │
│ 3155   │ 5     │ 1     │ 106   │ 0.0     │
│ 3156   │ 6     │ 1     │ 106   │ 0.0     │
│ 3157   │ 7     │ 1     │ 106   │ 0.0     │
│ 3158   │ 8     │ 1     │ 106   │ 0.0     │
│ 3159   │ 9     │ 1     │ 106   │ 0.0     │
│ 3160   │ 10    │ 1     │ 106   │ 0.0     │
│ 3161   │ 11    │ 1     │ 106   │ 0.0     │
│ 3162   │ 12    │ 1     │ 106   │ 0.0     │
│ 3163   │ 13    │ 1     │ 106   │ 0.0     │
│ 3164   │ 14    │ 1     │ 106   │ 0.0     │
│ 3165   │ 15    │ 1     │ 106   │ 0.0     │
│ 3166   │ 16    │ 1     │ 106   │ 0.0     │
│ 3167   │ 17    │ 1     │ 106   │ 0.0     │
│ 3168   │ 18    │ 1     │ 106   │ 0.0     │
│ 3169   │ 19    │ 1     │ 106   │ 0.0     │
│ 3170   │

Excessive output truncated after 524290 bytes.

 │ 27    │ 1     │ 108   │ 0.0     │
│ 3238   │ 28    │ 1     │ 108   │ 0.0     │
│ 3239   │ 29    │ 1     │ 108   │ 0.0     │
│ 3240   │ 30    │ 1     │ 108   │ 0.0     │
│ 3241   │ 1     │ 1     │ 109   │ 0.0     │
│ 3242   │ 2     │ 1     │ 109   │ 0.0     │
│ 3243   │ 3     │ 1     │ 109   │ 0.0     │
│ 3244   │ 4     │ 1     │ 109   │ 0.0     │
│ 3245   │ 5     │ 1     │ 109   │ 0.0     │
│ 3246   │ 6     │ 1     │ 109   │ 0.0     │
│ 3247   │ 7     │ 1     │ 109   │ 0.0     │
│ 3248   │ 8     │ 1     │ 109   │ 0.0     │
│ 3249   │ 9     │ 1     │ 109   │ 0.0     │
│ 3250   │ 10    │ 1     │ 109   │ 0.0     │
│ 3251   │ 11    │ 1     │ 109   │ 0.0     │
│ 3252   │ 12    │ 1     │ 109   │ 0.0     │
│ 3253   │ 13    │ 1     │ 109   │ 0.0     │
│ 3254   │ 14    │ 1     │ 109   │ 0.0     │
│ 3255   │ 15    │ 1     │ 109   │ 0.0     │
│ 3256   │ 16    │ 1     │ 109   │ 0.0     │
│ 3257   │ 17    │ 1     │ 109   │ 0.0     │
│ 3258   │ 18    │ 1     │ 109   │ 0.0     │
│ 3259   │ 19    │

0.5022666666666666

In [76]:
# Now we need a policy which randomly picks between the 2
function thomp_pol_func(Q_tables, N_tables, i, actions, s)
    # passed in i ignored, kept for consistency
    i = rand(1:2)
    #println("i:$i")
    # return 
#     if haskey(Q_tables[i], s)
#        # println("ucb: $(ucbs)")
#        val, idx = findmax(Q_tables[i][s])
#        #println("Selected $val, $idx from $(Q_tables[i][s]) for $i, $s")
#        #println("$(Q_tables[i][s])")
#        return action_map[idx]
#     else
#        act = action_map[rand(actions, 1)[1]]
#        println("random action $act") 
#        return act
#     end
    if i == 1
        return :left
    else
        return :right
    end
end

thomp_pol_func (generic function with 1 method)

In [77]:
#Now we run with that policy
include("./Agent.jl")
function run_thompson_chain_simulations(nruns, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
    runs = []
    for i in 1:nruns
        agents = Any[]
        num_states = 100
        num_actions = 2
        epochs=1
        thomp_policies = []
        H = floor(Int, 3 * num_states / 2)
        actions = [1, 2]
        action_map = Dict(1 => :left, :2 => :right)
        rev_action_map = Dict(:left => 1, :right => 2)
        states = 1:(num_states+2)
        #print("Before q's")
        true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,.9, theta)
        Q_tables_thomp = Dict(1 => Q_tables1[1], 2 => Q_tables2[1])
        N_tables_thomp = Dict(1 => N_tables1[1], 2 => N_tables2[1])
        #println("Q_T: $Q_tables_thomp")
        #println("N_T: $N_tables_thomp")
        for ag in 1:num_agents
          push!(thomp_policies, curry(curry(curry(curry(thomp_pol_func, Q_tables_thomp), N_tables_thomp),0), actions))
        end
        # push!(thomp_policies, curry(curry(curry(curry(thomp_pol_func, Q_tables_thomp), N_tables_thomp),0), actions))
        #println("after policies")
        (Q_tables3, N_tables3, trash) = PFAgent.setup_agents(states, num_states, num_agents,
                                                                    actions, num_actions, ucb_pol)

        mdps = [deepcopy(true_mdp) for ag in 1:num_agents]
        r_history = PFAgent.run_chain!(
                   policies=thomp_policies,
                   found_target=chain_found_target,
                   mdps=mdps,
                   update_Q=update_Q,
                   n_agents=num_agents,
                   n_states=num_states,
                   Q_tables=Q_tables3,
                   N_tables=N_tables3,
                   epochs=epochs,
                   steps=H,
                   rev_action_map=rev_action_map,
                   stop_early=true)

        R = (num_states - 2) / 2
        #println([r for (e,i,t,r) in r_history if i == 1])
        #println([r for (e,i,t,r) in r_history if i == 2])
        for (e, ag, t, st, r)  in r_history
          push!(runs, (i, e, ag, t, st, r)) 
        end
    end
    return runs
end

run_thompson_chain_simulations (generic function with 1 method)

In [80]:
num_agents = 10
results = run_thompson_chain_simulations(30, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
using CSV
using DataFrames
df_thomp = DataFrame(run = [x[1] for x in results], epoch = [x[2] for x in results], agent=[x[3] for x in results],
               time = [x[4] for x in results], state = [x[5] for x in results], reward = [x[6] for x in results])
#println(df_thomp)
#df_thomp

setup agents
e: 1, t: 1, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 2, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 2, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 1, t: 3, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 2, result: (s = 53, a = :left, r = -1, sp = 52, t = 2)
e: 1, t: 1, agent 3, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 1, t: 4, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 2, result: (s = 52, a = :left, r = -1, sp = 51, t = 3)
e: 1, t: 2, agent 3, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 1, t: 1, agent 4, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 5, agent 1, result: (s = 48, a = :right, r = -1, sp = 49, t = 5)
e: 1, t: 4, agent 2, result: (s = 51, a = :left, r = -1, sp = 50, t = 4)
e: 1, t: 3, agent 3, result: (s = 54, a = :left, r = -1, sp = 53, t = 3)
e: 1, t: 2, agent 4, result: (s = 

e: 1, t: 23, agent 3, result: (s = 52, a = :right, r = -1, sp = 53, t = 23)
e: 1, t: 22, agent 4, result: (s = 49, a = :right, r = -1, sp = 50, t = 22)
e: 1, t: 21, agent 5, result: (s = 56, a = :right, r = -1, sp = 57, t = 21)
e: 1, t: 20, agent 6, result: (s = 55, a = :left, r = -1, sp = 54, t = 20)
e: 1, t: 19, agent 7, result: (s = 52, a = :left, r = -1, sp = 51, t = 19)
e: 1, t: 18, agent 8, result: (s = 53, a = :left, r = -1, sp = 52, t = 18)
e: 1, t: 17, agent 9, result: (s = 50, a = :right, r = -1, sp = 51, t = 17)
e: 1, t: 16, agent 10, result: (s = 57, a = :left, r = -1, sp = 56, t = 16)
e: 1, t: 26, agent 1, result: (s = 55, a = :right, r = -1, sp = 56, t = 26)
e: 1, t: 25, agent 2, result: (s = 42, a = :right, r = -1, sp = 43, t = 25)
e: 1, t: 24, agent 3, result: (s = 53, a = :right, r = -1, sp = 54, t = 24)
e: 1, t: 23, agent 4, result: (s = 50, a = :right, r = -1, sp = 51, t = 23)
e: 1, t: 22, agent 5, result: (s = 57, a = :left, r = -1, sp = 56, t = 22)
e: 1, t: 21, age

e: 1, t: 30, agent 9, result: (s = 45, a = :right, r = -1, sp = 46, t = 30)
e: 1, t: 29, agent 10, result: (s = 52, a = :right, r = -1, sp = 53, t = 29)
e: 1, t: 39, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 39)
e: 1, t: 38, agent 2, result: (s = 45, a = :left, r = -1, sp = 44, t = 38)
e: 1, t: 37, agent 3, result: (s = 56, a = :right, r = -1, sp = 57, t = 37)
e: 1, t: 36, agent 4, result: (s = 49, a = :right, r = -1, sp = 50, t = 36)
e: 1, t: 35, agent 5, result: (s = 50, a = :left, r = -1, sp = 49, t = 35)
e: 1, t: 34, agent 6, result: (s = 51, a = :right, r = -1, sp = 52, t = 34)
e: 1, t: 33, agent 7, result: (s = 58, a = :left, r = -1, sp = 57, t = 33)
e: 1, t: 32, agent 8, result: (s = 53, a = :right, r = -1, sp = 54, t = 32)
e: 1, t: 31, agent 9, result: (s = 46, a = :right, r = -1, sp = 47, t = 31)
e: 1, t: 30, agent 10, result: (s = 53, a = :right, r = -1, sp = 54, t = 30)
e: 1, t: 40, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 40)
e: 1, t: 39, ag

e: 1, t: 48, agent 5, result: (s = 51, a = :right, r = -1, sp = 52, t = 48)
e: 1, t: 47, agent 6, result: (s = 52, a = :left, r = -1, sp = 51, t = 47)
e: 1, t: 46, agent 7, result: (s = 59, a = :left, r = -1, sp = 58, t = 46)
e: 1, t: 45, agent 8, result: (s = 52, a = :right, r = -1, sp = 53, t = 45)
e: 1, t: 44, agent 9, result: (s = 45, a = :right, r = -1, sp = 46, t = 44)
e: 1, t: 43, agent 10, result: (s = 54, a = :right, r = -1, sp = 55, t = 43)
e: 1, t: 53, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 53)
e: 1, t: 52, agent 2, result: (s = 43, a = :right, r = -1, sp = 44, t = 52)
e: 1, t: 51, agent 3, result: (s = 60, a = :right, r = -1, sp = 61, t = 51)
e: 1, t: 50, agent 4, result: (s = 45, a = :right, r = -1, sp = 46, t = 50)
e: 1, t: 49, agent 5, result: (s = 52, a = :left, r = -1, sp = 51, t = 49)
e: 1, t: 48, agent 6, result: (s = 51, a = :left, r = -1, sp = 50, t = 48)
e: 1, t: 47, agent 7, result: (s = 58, a = :right, r = -1, sp = 59, t = 47)
e: 1, t: 46, ag

e: 1, t: 66, agent 1, result: (s = 55, a = :left, r = -1, sp = 54, t = 66)
e: 1, t: 65, agent 2, result: (s = 44, a = :right, r = -1, sp = 45, t = 65)
e: 1, t: 64, agent 3, result: (s = 61, a = :right, r = -1, sp = 62, t = 64)
e: 1, t: 63, agent 4, result: (s = 42, a = :right, r = -1, sp = 43, t = 63)
e: 1, t: 62, agent 5, result: (s = 49, a = :left, r = -1, sp = 48, t = 62)
e: 1, t: 61, agent 6, result: (s = 52, a = :right, r = -1, sp = 53, t = 61)
e: 1, t: 60, agent 7, result: (s = 61, a = :left, r = -1, sp = 60, t = 60)
e: 1, t: 59, agent 8, result: (s = 50, a = :right, r = -1, sp = 51, t = 59)
e: 1, t: 58, agent 9, result: (s = 47, a = :left, r = -1, sp = 46, t = 58)
e: 1, t: 57, agent 10, result: (s = 50, a = :left, r = -1, sp = 49, t = 57)
e: 1, t: 67, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 67)
e: 1, t: 66, agent 2, result: (s = 45, a = :left, r = -1, sp = 44, t = 66)
e: 1, t: 65, agent 3, result: (s = 62, a = :right, r = -1, sp = 63, t = 65)
e: 1, t: 64, agent

...

e: 1, t: 56, agent 3, result: (s = 55, a = :left, r = -1, sp = 54, t = 56)
e: 1, t: 55, agent 4, result: (s = 54, a = :right, r = -1, sp = 55, t = 55)
e: 1, t: 54, agent 5, result: (s = 45, a = :right, r = -1, sp = 46, t = 54)
e: 1, t: 53, agent 6, result: (s = 50, a = :right, r = -1, sp = 51, t = 53)
e: 1, t: 52, agent 7, result: (s = 49, a = :left, r = -1, sp = 48, t = 52)
e: 1, t: 51, agent 8, result: (s = 60, a = :left, r = -1, sp = 59, t = 51)
e: 1, t: 50, agent 9, result: (s = 49, a = :left, r = -1, sp = 48, t = 50)
e: 1, t: 49, agent 10, result: (s = 46, a = :right, r = -1, sp = 47, t = 49)
e: 1, t: 59, agent 1, result: (s = 48, a = :right, r = -1, sp = 49, t = 59)
e: 1, t: 58, agent 2, result: (s = 49, a = :left, r = -1, sp = 48, t = 58)
e: 1, t: 57, agent 3, result: (s = 54, a = :right, r = -1, sp = 55, t = 57)
e: 1, t: 56, agent 4, result: (s = 55, a = :right, r = -1, sp = 56, t = 56)
e: 1, t: 55, agent 5, result: (s = 46, a = :right, r = -1, sp = 47, t = 55)
e: 1, t: 54, age

e: 1, t: 63, agent 9, result: (s = 52, a = :right, r = -1, sp = 53, t = 63)
e: 1, t: 62, agent 10, result: (s = 43, a = :left, r = -1, sp = 42, t = 62)
e: 1, t: 72, agent 1, result: (s = 45, a = :left, r = -1, sp = 44, t = 72)
e: 1, t: 71, agent 2, result: (s = 46, a = :left, r = -1, sp = 45, t = 71)
e: 1, t: 70, agent 3, result: (s = 55, a = :right, r = -1, sp = 56, t = 70)
e: 1, t: 69, agent 4, result: (s = 50, a = :left, r = -1, sp = 49, t = 69)
e: 1, t: 68, agent 5, result: (s = 53, a = :right, r = -1, sp = 54, t = 68)
e: 1, t: 67, agent 6, result: (s = 50, a = :right, r = -1, sp = 51, t = 67)
e: 1, t: 66, agent 7, result: (s = 49, a = :right, r = -1, sp = 50, t = 66)
e: 1, t: 65, agent 8, result: (s = 64, a = :left, r = -1, sp = 63, t = 65)
e: 1, t: 64, agent 9, result: (s = 53, a = :right, r = -1, sp = 54, t = 64)
e: 1, t: 63, agent 10, result: (s = 42, a = :left, r = -1, sp = 41, t = 63)
e: 1, t: 73, agent 1, result: (s = 44, a = :left, r = -1, sp = 43, t = 73)
e: 1, t: 72, agen

Excessive output truncated after 524351 bytes.

e: 1, t: 81, agent 5, result: (s = 54, a = :right, r = -1, sp = 55, t = 81)
e: 1, t: 80, agent 6, result: (s = 47, a = :left, r = -1, sp = 46, t = 80)
e: 1, t: 79, agent 7, result: (s = 54, a = :right, r = -1, sp = 55, t = 79)
e: 1, t: 78, agent 8, result: (s = 67, a = :left, r = -1, sp = 66, t = 78)
e: 1, t: 77, agent 9, result: (s = 52, a = :right, r = -1, sp = 53, t = 77)
e: 1, t: 76, agent 10, result: (s = 39, a = :right, r = -1, sp = 40, t = 76)
e: 1, t: 86, agent 1, result: (s = 39, a = :right, r = -1, sp = 40, t = 86)
e: 1, t: 85, agent 2, result: (s = 46, a = :left, r = -1, sp = 45, t = 85)
e: 1, t: 84, agent 3, result: (s = 61, a = :left, r = -1, sp = 60, t = 84)
e: 1, t: 83, agent 4, result: (s = 50, a = :right, r = -1, sp = 51, t = 83)
e: 1, t: 82, agent 5, result: (s = 55, a = :right, r = -1, sp = 56, t = 82)
e: 1, t: 81, agent 6, result: (s = 46, a = :right, r = -1, sp = 47, t = 81)
e: 1, t: 80, agent 7, result: (s = 55, a = :left, r = -1, sp = 54, t = 80)
e: 1, t: 79, age

45000×6 DataFrame
│ Row   │ run   │ epoch │ agent │ time  │ state │ reward │
│       │ Int64 │ Int64 │ Int64 │ Int64 │ Int64 │ Int64  │
├───────┼───────┼───────┼───────┼───────┼───────┼────────┤
│ 1     │ 1     │ 1     │ 1     │ 1     │ 52    │ -1     │
│ 2     │ 1     │ 1     │ 1     │ 2     │ 51    │ -1     │
│ 3     │ 1     │ 1     │ 2     │ 1     │ 52    │ -1     │
│ 4     │ 1     │ 1     │ 1     │ 3     │ 50    │ -1     │
│ 5     │ 1     │ 1     │ 2     │ 2     │ 53    │ -1     │
│ 6     │ 1     │ 1     │ 3     │ 1     │ 52    │ -1     │
│ 7     │ 1     │ 1     │ 1     │ 4     │ 49    │ -1     │
│ 8     │ 1     │ 1     │ 2     │ 3     │ 52    │ -1     │
│ 9     │ 1     │ 1     │ 3     │ 2     │ 53    │ -1     │
│ 10    │ 1     │ 1     │ 4     │ 1     │ 52    │ -1     │
⋮
│ 44990 │ 30    │ 1     │ 10    │ 146   │ 55    │ -1     │
│ 44991 │ 30    │ 1     │ 7     │ 150   │ 35    │ -1     │
│ 44992 │ 30    │ 1     │ 8     │ 149   │ 58    │ -1     │
│ 44993 │ 30    │ 1     │ 9     │ 148   │ 61    │ -1     │
│ 44994 │ 30    │ 1     │ 10    │ 147   │ 56    │ -1     │
│ 44995 │ 30    │ 1     │ 8     │ 150   │ 59    │ -1     │
│ 44996 │ 30    │ 1     │ 9     │ 149   │ 62    │ -1     │
│ 44997 │ 30    │ 1     │ 10    │ 148   │ 55    │ -1     │
│ 44998 │ 30    │ 1     │ 9     │ 150   │ 61    │ -1     │
│ 44999 │ 30    │ 1     │ 10    │ 149   │ 56    │ -1     │
│ 45000 │ 30    │ 1     │ 10    │ 150   │ 55    │ -1     │

In [81]:

get_average_regret(df_thomp, num_agents)




300×4 DataFrame
│ Row │ run   │ epoch │ agent │ Regret  │
│     │ Int64 │ Int64 │ Int64 │ Float64 │
├─────┼───────┼───────┼───────┼─────────┤
│ 1   │ 1     │ 1     │ 1     │ 225.0   │
│ 2   │ 1     │ 1     │ 2     │ 225.0   │
│ 3   │ 1     │ 1     │ 3     │ 225.0   │
│ 4   │ 1     │ 1     │ 4     │ 225.0   │
│ 5   │ 1     │ 1     │ 5     │ 225.0   │
│ 6   │ 1     │ 1     │ 6     │ 225.0   │
│ 7   │ 1     │ 1     │ 7     │ 225.0   │
│ 8   │ 1     │ 1     │ 8     │ 225.0   │
│ 9   │ 1     │ 1     │ 9     │ 225.0   │
│ 10  │ 1     │ 1     │ 10    │ 225.0   │
│ 11  │ 2     │ 1     │ 1     │ 225.0   │
│ 12  │ 2     │ 1     │ 2     │ 225.0   │
│ 13  │ 2     │ 1     │ 3     │ 225.0   │
│ 14  │ 2     │ 1     │ 4     │ 225.0   │
│ 15  │ 2     │ 1     │ 5     │ 225.0   │
│ 16  │ 2     │ 1     │ 6     │ 225.0   │
│ 17  │ 2     │ 1     │ 7     │ 225.0   │
│ 18  │ 2     │ 1     │ 8     │ 225.0   │
│ 19  │ 2     │ 1     │ 9     │ 225.0   │
│ 20  │ 2     │ 1     │ 10    │ 225.0   │
│ 21  │ 3     │ 1 

├─────┼───────┼───────┼───────┼─────────┤
│ 1   │ 1     │ 1     │ 1     │ 225.0   │
│ 2   │ 1     │ 1     │ 2     │ 225.0   │
│ 3   │ 1     │ 1     │ 3     │ 225.0   │
│ 4   │ 1     │ 1     │ 4     │ 225.0   │
│ 5   │ 1     │ 1     │ 5     │ 225.0   │
│ 6   │ 1     │ 1     │ 6     │ 225.0   │
│ 7   │ 1     │ 1     │ 7     │ 225.0   │
│ 8   │ 1     │ 1     │ 8     │ 225.0   │
│ 9   │ 1     │ 1     │ 9     │ 225.0   │
│ 10  │ 1     │ 1     │ 10    │ 225.0   │
│ 11  │ 2     │ 1     │ 1     │ 225.0   │
│ 12  │ 2     │ 1     │ 2     │ 225.0   │
│ 13  │ 2     │ 1     │ 3     │ 225.0   │
│ 14  │ 2     │ 1     │ 4     │ 225.0   │
│ 15  │ 2     │ 1     │ 5     │ 225.0   │
│ 16  │ 2     │ 1     │ 6     │ 225.0   │
│ 17  │ 2     │ 1     │ 7     │ 225.0   │
│ 18  │ 2     │ 1     │ 8     │ 225.0   │
│ 19  │ 2     │ 1     │ 9     │ 225.0   │
│ 20  │ 2     │ 1     │ 10    │ 225.0   │
│ 21  │ 3     │ 1     │ 1     │ 225.0   │
│ 22  │ 3     │ 1     │ 2     │ 225.0   │
│ 23  │ 3     │ 1     │ 3     │ 22

│ 288 │ 29    │ 1     │ 8     │ 225.0   │
│ 289 │ 29    │ 1     │ 9     │ 225.0   │
│ 290 │ 29    │ 1     │ 10    │ 225.0   │
│ 291 │ 30    │ 1     │ 1     │ 225.0   │
│ 292 │ 30    │ 1     │ 2     │ 225.0   │
│ 293 │ 30    │ 1     │ 3     │ 225.0   │
│ 294 │ 30    │ 1     │ 4     │ 225.0   │
│ 295 │ 30    │ 1     │ 5     │ 225.0   │
│ 296 │ 30    │ 1     │ 6     │ 225.0   │
│ 297 │ 30    │ 1     │ 7     │ 225.0   │
│ 298 │ 30    │ 1     │ 8     │ 225.0   │
│ 299 │ 30    │ 1     │ 9     │ 225.0   │
│ 300 │ 30    │ 1     │ 10    │ 225.0   │

225.0

In [36]:
# Policies are chosen outside.
function seed_pol_func(Q_tables, N_tables, i, actions, s)
    # passed in i ignored, kept for consistency
    # i = rand(1:length(Q_tables))
    #println("i:$i")
    # return 
    if haskey(Q_tables[i], s)
       # println("ucb: $(ucbs)")
       val, idx = findmax(Q_tables[i][s])
       #println("Selected $val, $idx from $(Q_tables[i][s]) for $i, $s")
       #print("$(Q_tables[i][s])")
       return action_map[idx]
    else
       act = action_map[rand(actions, 1)[1]]
       println("random action $act") 
       return act
    end
end

seed_pol_func (generic function with 1 method)

In [37]:
function seed_pol_func(i,  s)
    # passed in i ignored, kept for consistency
    # i = rand(1:length(Q_tables))
    #println("i:$i")
    # return 
       return [:left, :right][i]
end

seed_pol_func (generic function with 2 methods)

In [38]:
#Now we run with that policy
include("./Agent.jl")
using StatsBase
function run_seed_chain_simulations(nruns, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
    runs = []
    (Q_tables3, N_tables3, trash) = PFAgent.setup_agents(states, num_states, num_agents,
                                                                actions, num_actions, ucb_pol)
    for i in 1:nruns
        agents = Any[]
        num_states = 100
        num_actions = 2
        epochs=1
        seed_policies = []
        H = floor(Int, 3 * num_states / 2)
        actions = [1, 2]
        action_map = Dict(1 => :left, :2 => :right)
        rev_action_map = Dict(:left => 1, :right => 2)
        states = 1:(num_states+2)
        #print("Before q's")
        true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,1.0, theta)
        #Q_tables_list = [Q_tables1[1], Q_tables2[1]]
        #N_tables_list = [N_tables1[1], N_tables2[1]]
        # so diff with thompson sampling is that we should do the rand now
        #Q_tables_seed = Dict(i => Q_tables_list[rand(1:length(Q_tables_list))] for i in 1:num_agents)
        #N_tables_seed = Dict(i => N_tables_list[rand(1:length(N_tables_list))] for i in 1:num_agents)
        
        for ag in 1:num_agents
            #println("Q_T: $Q_tables_thomp")
            #println("N_T: $N_tables_thomp")
            # push!(seed_policies, curry(curry(curry(curry(seed_pol_func, Q_tables_seed), N_tables_seed),ag), actions))
            # push!(seed_policies, curry(curry(curry(curry(seed_pol_func, Q_tables_seed), N_tables_seed),2), actions))
            push!(seed_policies, curry(seed_pol_func, rand(Bernoulli(0.5))+1))
        end
        #println("after policies")
        #(Q_tables3, N_tables3, trash) = PFAgent.setup_agents(states, num_states, num_agents,
        #                                                            actions, num_actions, ucb_pol)
        mdps = [deepcopy(true_mdp) for ag in 1:num_agents]
        r_history = PFAgent.run_chain!(
                   policies=seed_policies,
                   found_target=chain_found_target,
                   mdps=mdps,
                   update_Q=update_Q,
                   n_agents=num_agents,
                   n_states=num_states,
                   Q_tables=Q_tables3,
                   N_tables=N_tables3,
                   epochs=epochs,
                   steps=H,
                   rev_action_map=rev_action_map,
                   stop_early=true)

        R = (num_states - 2) / 2
        #println([r for (e,i,t,r) in r_history if i == 1])
        #println([r for (e,i,t,r) in r_history if i == 2])
        print(r_history)
        #reg = R - sum([r for (e,ag,t,r) in r_history if ag == an_ag end 0])
        for (e, ag, t, st, r)  in r_history
          push!(runs, (i, e, ag, t, st, r)) 
        end
        #reg_a2 = R - sum([r for (e,ag,t,r) in r_history if ag == 2])
    end
    return runs
end                                    
                                    

run_seed_chain_simulations (generic function with 1 method)

In [45]:

include("./Agent.jl")
# Base setup 

# Solution

# solve mdp in both directions
# Then each agent will pick on of the policies.
# common
num_agents = 1
agents = Any[]
num_states = 100
num_actions = 2
epochs = 100
H = floor(Int, 3 * num_states / 2)
actions = [1, 2]
action_map = Dict(1 => :left, :2 => :right)
rev_action_map = Dict(:left => 1, :right => 2)
states = 1:(num_states+2)


theta = 10


(Q_tables1, N_tables1, policies1) = PFAgent.setup_agents(states, num_states, num_agents,
                                                            actions, num_actions, ucb_pol)

true_mdp = PFChainMDP.PChainMDP(num_states+2,1.0,.99, theta)
PFAgent.run_chain!(policies=policies1,
           found_target=chain_found_target,
           mdps=[true_mdp],
           update_Q=update_Q,
           n_agents=num_agents,
           n_states=num_states,
           Q_tables=Q_tables1,
           N_tables=N_tables1,
           epochs=epochs,
           steps=H,
           rev_action_map=rev_action_map,
           stop_early=false)

# theta = -10
using JSON
println("Q1:$(json(Q_tables1,2))")
println("N1:$(json(N_tables1,2))")

true_mdp2 = PFChainMDP.PChainMDP(num_states+2,1.0,.99, -theta)
(Q_tables2, N_tables2, policies2) = PFAgent.setup_agents(states, num_states, num_agents,
                                                            actions, num_actions, ucb_pol)
PFAgent.run_chain!(policies=policies2,
           found_target=chain_found_target,
           mdps=[true_mdp2],
           update_Q=update_Q,
           n_agents=num_agents,
           n_states=num_states,
           Q_tables=Q_tables2,
           N_tables=N_tables2,
           epochs=epochs,
           steps=H,
           rev_action_map=rev_action_map,
           stop_early=false)



println("Q2: $(json(Q_tables2[1],2))")
println("N2: $(json(N_tables2[1],2))")

setup agents


e: 10, t: 1, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 10, t: 2, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 10, t: 3, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 3)
e: 10, t: 4, agent 1, result: (s = 55, a = :right, r = -1, sp = 56, t = 4)
e: 10, t: 5, agent 1, result: (s = 56, a = :right, r = -1, sp = 57, t = 5)
e: 10, t: 6, agent 1, result: (s = 57, a = :right, r = -1, sp = 58, t = 6)
e: 10, t: 7, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 7)
e: 10, t: 8, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 8)
e: 10, t: 9, agent 1, result: (s = 60, a = :right, r = -1, sp = 61, t = 9)
e: 10, t: 10, agent 1, result: (s = 61, a = :right, r = -1, sp = 62, t = 10)
e: 10, t: 11, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 11)
e: 10, t: 12, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 12)
e: 10, t: 13, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 13)
e: 10, t: 14, agen

e: 10, t: 135, agent 1, result: (s = 74, a = :right, r = -1, sp = 75, t = 135)
e: 10, t: 136, agent 1, result: (s = 75, a = :right, r = -1, sp = 76, t = 136)
e: 10, t: 137, agent 1, result: (s = 76, a = :right, r = -1, sp = 77, t = 137)
e: 10, t: 138, agent 1, result: (s = 77, a = :right, r = -1, sp = 78, t = 138)
e: 10, t: 139, agent 1, result: (s = 78, a = :left, r = -1, sp = 77, t = 139)
e: 10, t: 140, agent 1, result: (s = 77, a = :left, r = -1, sp = 76, t = 140)
e: 10, t: 141, agent 1, result: (s = 76, a = :left, r = -1, sp = 75, t = 141)
e: 10, t: 142, agent 1, result: (s = 75, a = :left, r = -1, sp = 74, t = 142)
e: 10, t: 143, agent 1, result: (s = 74, a = :left, r = -1, sp = 73, t = 143)
e: 10, t: 144, agent 1, result: (s = 73, a = :left, r = -1, sp = 72, t = 144)
e: 10, t: 145, agent 1, result: (s = 72, a = :left, r = -1, sp = 71, t = 145)
e: 10, t: 146, agent 1, result: (s = 71, a = :right, r = -1, sp = 72, t = 146)
e: 10, t: 147, agent 1, result: (s = 72, a = :right, r = -1

e: 20, t: 119, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 119)
e: 20, t: 120, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 120)
e: 20, t: 121, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 121)
e: 20, t: 122, agent 1, result: (s = 55, a = :left, r = -1, sp = 54, t = 122)
e: 20, t: 123, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 123)
e: 20, t: 124, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 124)
e: 20, t: 125, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 125)
e: 20, t: 126, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 126)
e: 20, t: 127, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 127)
e: 20, t: 128, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 128)
e: 20, t: 129, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 129)
e: 20, t: 130, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 130)
e: 20, t: 131, agent 1, result: (s = 54, a = :left, r = -

e: 30, t: 103, agent 1, result: (s = 64, a = :left, r = -1, sp = 63, t = 103)
e: 30, t: 104, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 104)
e: 30, t: 105, agent 1, result: (s = 62, a = :left, r = -1, sp = 61, t = 105)
e: 30, t: 106, agent 1, result: (s = 61, a = :left, r = -1, sp = 60, t = 106)
e: 30, t: 107, agent 1, result: (s = 60, a = :left, r = -1, sp = 59, t = 107)
e: 30, t: 108, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 108)
e: 30, t: 109, agent 1, result: (s = 58, a = :right, r = -1, sp = 59, t = 109)
e: 30, t: 110, agent 1, result: (s = 59, a = :right, r = -1, sp = 60, t = 110)
e: 30, t: 111, agent 1, result: (s = 60, a = :left, r = -1, sp = 59, t = 111)
e: 30, t: 112, agent 1, result: (s = 59, a = :left, r = -1, sp = 58, t = 112)
e: 30, t: 113, agent 1, result: (s = 58, a = :left, r = -1, sp = 57, t = 113)
e: 30, t: 114, agent 1, result: (s = 57, a = :left, r = -1, sp = 56, t = 114)
e: 30, t: 115, agent 1, result: (s = 56, a = :left, r = -1, sp

...

e: 70, t: 119, agent 1, result: (s = 48, a = :right, r = -1, sp = 49, t = 119)
e: 70, t: 120, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 120)
e: 70, t: 121, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 121)
e: 70, t: 122, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 122)
e: 70, t: 123, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 123)
e: 70, t: 124, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 124)
e: 70, t: 125, agent 1, result: (s = 48, a = :left, r = -1, sp = 47, t = 125)
e: 70, t: 126, agent 1, result: (s = 47, a = :left, r = -1, sp = 46, t = 126)
e: 70, t: 127, agent 1, result: (s = 46, a = :left, r = -1, sp = 45, t = 127)
e: 70, t: 128, agent 1, result: (s = 45, a = :left, r = -1, sp = 44, t = 128)
e: 70, t: 129, agent 1, result: (s = 44, a = :right, r = -1, sp = 45, t = 129)
e: 70, t: 130, agent 1, result: (s = 45, a = :right, r = -1, sp = 46, t = 130)
e: 70, t: 131, agent 1, result: (s = 46, a = :right, r = -1

e: 80, t: 103, agent 1, result: (s = 64, a = :right, r = -1, sp = 65, t = 103)
e: 80, t: 104, agent 1, result: (s = 65, a = :right, r = -1, sp = 66, t = 104)
e: 80, t: 105, agent 1, result: (s = 66, a = :left, r = -1, sp = 65, t = 105)
e: 80, t: 106, agent 1, result: (s = 65, a = :left, r = -1, sp = 64, t = 106)
e: 80, t: 107, agent 1, result: (s = 64, a = :left, r = -1, sp = 63, t = 107)
e: 80, t: 108, agent 1, result: (s = 63, a = :left, r = -1, sp = 62, t = 108)
e: 80, t: 109, agent 1, result: (s = 62, a = :left, r = -1, sp = 61, t = 109)
e: 80, t: 110, agent 1, result: (s = 61, a = :left, r = -1, sp = 60, t = 110)
e: 80, t: 111, agent 1, result: (s = 60, a = :right, r = -1, sp = 61, t = 111)
e: 80, t: 112, agent 1, result: (s = 61, a = :right, r = -1, sp = 62, t = 112)
e: 80, t: 113, agent 1, result: (s = 62, a = :right, r = -1, sp = 63, t = 113)
e: 80, t: 114, agent 1, result: (s = 63, a = :right, r = -1, sp = 64, t = 114)
e: 80, t: 115, agent 1, result: (s = 64, a = :right, r = -

e: 90, t: 86, agent 1, result: (s = 55, a = :left, r = -1, sp = 54, t = 86)
e: 90, t: 87, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 87)
e: 90, t: 88, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 88)
e: 90, t: 89, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 89)
e: 90, t: 90, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 90)
e: 90, t: 91, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 91)
e: 90, t: 92, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 92)
e: 90, t: 93, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 93)
e: 90, t: 94, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 94)
e: 90, t: 95, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 95)
e: 90, t: 96, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 96)
e: 90, t: 97, agent 1, result: (s = 54, a = :right, r = -1, sp = 55, t = 97)
e: 90, t: 98, agent 1, result: (s = 55, a = :right, r = -1, sp = 56, t = 98)
e: 90

e: 100, t: 72, agent 1, result: (s = 47, a = :right, r = -1, sp = 48, t = 72)
e: 100, t: 73, agent 1, result: (s = 48, a = :right, r = -1, sp = 49, t = 73)
e: 100, t: 74, agent 1, result: (s = 49, a = :right, r = -1, sp = 50, t = 74)
e: 100, t: 75, agent 1, result: (s = 50, a = :right, r = -1, sp = 51, t = 75)
e: 100, t: 76, agent 1, result: (s = 51, a = :right, r = -1, sp = 52, t = 76)
e: 100, t: 77, agent 1, result: (s = 52, a = :right, r = -1, sp = 53, t = 77)
e: 100, t: 78, agent 1, result: (s = 53, a = :right, r = -1, sp = 54, t = 78)
e: 100, t: 79, agent 1, result: (s = 54, a = :left, r = -1, sp = 53, t = 79)
e: 100, t: 80, agent 1, result: (s = 53, a = :left, r = -1, sp = 52, t = 80)
e: 100, t: 81, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 81)
e: 100, t: 82, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 82)
e: 100, t: 83, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 83)
e: 100, t: 84, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, 

N2: [
  [
    0.0,
    0.0,
    1.0,
    2.0,
    2.0,
    2.0,
    2.0,
    2.0,
    2.0,
    2.0,
    2.0,
    3.0,
    4.0,
    5.0,
    6.0,
    7.0,
    9.0,
    10.0,
    12.0,
    14.0,
    17.0,
    19.0,
    21.0,
    22.0,
    24.0,
    27.0,
    31.0,
    34.0,
    37.0,
    39.0,
    43.0,
    47.0,
    53.0,
    59.0,
    66.0,
    72.0,
    80.0,
    87.0,
    99.0,
    110.0,
    123.0,
    136.0,
    152.0,
    168.0,
    190.0,
    211.0,
    235.0,
    259.0,
    290.0,
    320.0,
    354.0,
    387.0,
    335.0,
    301.0,
    275.0,
    249.0,
    228.0,
    206.0,
    189.0,
    171.0,
    158.0,
    144.0,
    131.0,
    117.0,
    106.0,
    94.0,
    84.0,
    73.0,
    66.0,
    59.0,
    54.0,
    49.0,
    46.0,
    43.0,
    40.0,
    36.0,
    33.0,
    29.0,
    26.0,
    24.0,
    22.0,
    20.0,
    19.0,
    16.0,
    14.0,
    12.0,
    10.0,
    9.0,
    8.0,
    7.0,
    7.0,
    7.0,
    6.0,
    5.0,
    4.0,
    3.0,
    3.0,
    2.0,
    1.0,
   

In [71]:
num_agents = 10000
results = run_seed_chain_simulations(10, Q_tables1, Q_tables2, N_tables1, N_tables2, num_agents)
using CSV
using DataFrames
df = DataFrame(run = [x[1] for x in results], epoch = [x[2] for x in results], agent=[x[3] for x in results],
               time = [x[4] for x in results], state = [x[5] for x in results], reward = [x[6] for x in results])
println(df)
CSV.write("seed_chain_simulation.csv", df)
df

setup agents
e: 1, t: 1, agent 1, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 2, agent 1, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 2, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 1, t: 3, agent 1, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 2, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 1, t: 1, agent 3, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 4, agent 1, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 2, result: (s = 54, a = :right, r = -1, sp = 55, t = 3)
e: 1, t: 2, agent 3, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 4, result: (s = 52, a = :right, r = -1, sp = 53, t = 1)
e: 1, t: 5, agent 1, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 2, result: (s = 55, a = :right, r = -1, sp = 56, t = 4)
e: 1, t: 3, agent 3, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 4, result: (s =

e: 1, t: 14, agent 4, result: (s = 65, a = :right, r = -1, sp = 66, t = 14)
e: 1, t: 13, agent 5, result: (s = 64, a = :right, r = -1, sp = 65, t = 13)
e: 1, t: 12, agent 6, result: (s = 63, a = :right, r = -1, sp = 64, t = 12)
e: 1, t: 11, agent 7, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 8, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 9, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 10, result: (s = 59, a = :right, r = -1, sp = 60, t = 8)
e: 1, t: 7, agent 11, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 12, result: (s = 47, a = :left, r = -1, sp = 46, t = 6)
e: 1, t: 5, agent 13, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 14, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 15, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 16, result: (s = 51, a = :left, r = -1, sp = 50, t = 2)
e: 1, t: 1, agent 17, result: 

e: 1, t: 24, agent 1, result: (s = 29, a = :left, r = -1, sp = 28, t = 24)
e: 1, t: 23, agent 2, result: (s = 74, a = :right, r = -1, sp = 75, t = 23)
e: 1, t: 22, agent 3, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 4, result: (s = 72, a = :right, r = -1, sp = 73, t = 21)
e: 1, t: 20, agent 5, result: (s = 71, a = :right, r = -1, sp = 72, t = 20)
e: 1, t: 19, agent 6, result: (s = 70, a = :right, r = -1, sp = 71, t = 19)
e: 1, t: 18, agent 7, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 8, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 9, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 10, result: (s = 66, a = :right, r = -1, sp = 67, t = 15)
e: 1, t: 14, agent 11, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 12, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 13, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, age

e: 1, t: 23, agent 7, result: (s = 30, a = :left, r = -1, sp = 29, t = 23)
e: 1, t: 22, agent 8, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 9, result: (s = 32, a = :left, r = -1, sp = 31, t = 21)
e: 1, t: 20, agent 10, result: (s = 71, a = :right, r = -1, sp = 72, t = 20)
e: 1, t: 19, agent 11, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 12, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 13, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 14, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 15, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 16, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 17, result: (s = 64, a = :right, r = -1, sp = 65, t = 13)
e: 1, t: 12, agent 18, result: (s = 63, a = :right, r = -1, sp = 64, t = 12)
e: 1, t: 11, agent 19, result: (s = 62, a = :right, r = -1, sp = 63, t = 11)
e: 1, t: 10

e: 1, t: 13, agent 21, result: (s = 64, a = :right, r = -1, sp = 65, t = 13)
e: 1, t: 12, agent 22, result: (s = 63, a = :right, r = -1, sp = 64, t = 12)
e: 1, t: 11, agent 23, result: (s = 62, a = :right, r = -1, sp = 63, t = 11)
e: 1, t: 10, agent 24, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 25, result: (s = 60, a = :right, r = -1, sp = 61, t = 9)
e: 1, t: 8, agent 26, result: (s = 59, a = :right, r = -1, sp = 60, t = 8)
e: 1, t: 7, agent 27, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 28, result: (s = 57, a = :right, r = -1, sp = 58, t = 6)
e: 1, t: 5, agent 29, result: (s = 48, a = :left, r = -1, sp = 47, t = 5)
e: 1, t: 4, agent 30, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 31, result: (s = 50, a = :left, r = -1, sp = 49, t = 3)
e: 1, t: 2, agent 32, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 1, t: 1, agent 33, result: (s = 52, a = :left, r = -1, sp = 51, t = 1)
e: 1, t: 34, agent 1, r

...

e: 1, t: 14, agent 4, result: (s = 65, a = :right, r = -1, sp = 66, t = 14)
e: 1, t: 13, agent 5, result: (s = 64, a = :right, r = -1, sp = 65, t = 13)
e: 1, t: 12, agent 6, result: (s = 41, a = :left, r = -1, sp = 40, t = 12)
e: 1, t: 11, agent 7, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 10, agent 8, result: (s = 43, a = :left, r = -1, sp = 42, t = 10)
e: 1, t: 9, agent 9, result: (s = 44, a = :left, r = -1, sp = 43, t = 9)
e: 1, t: 8, agent 10, result: (s = 45, a = :left, r = -1, sp = 44, t = 8)
e: 1, t: 7, agent 11, result: (s = 46, a = :left, r = -1, sp = 45, t = 7)
e: 1, t: 6, agent 12, result: (s = 47, a = :left, r = -1, sp = 46, t = 6)
e: 1, t: 5, agent 13, result: (s = 56, a = :right, r = -1, sp = 57, t = 5)
e: 1, t: 4, agent 14, result: (s = 49, a = :left, r = -1, sp = 48, t = 4)
e: 1, t: 3, agent 15, result: (s = 54, a = :right, r = -1, sp = 55, t = 3)
e: 1, t: 2, agent 16, result: (s = 53, a = :right, r = -1, sp = 54, t = 2)
e: 1, t: 1, agent 17, result:

e: 1, t: 24, agent 1, result: (s = 75, a = :right, r = -1, sp = 76, t = 24)
e: 1, t: 23, agent 2, result: (s = 74, a = :right, r = -1, sp = 75, t = 23)
e: 1, t: 22, agent 3, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 4, result: (s = 72, a = :right, r = -1, sp = 73, t = 21)
e: 1, t: 20, agent 5, result: (s = 71, a = :right, r = -1, sp = 72, t = 20)
e: 1, t: 19, agent 6, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 7, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 8, result: (s = 36, a = :left, r = -1, sp = 35, t = 17)
e: 1, t: 16, agent 9, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 10, result: (s = 38, a = :left, r = -1, sp = 37, t = 15)
e: 1, t: 14, agent 11, result: (s = 39, a = :left, r = -1, sp = 38, t = 14)
e: 1, t: 13, agent 12, result: (s = 40, a = :left, r = -1, sp = 39, t = 13)
e: 1, t: 12, agent 13, result: (s = 63, a = :right, r = -1, sp = 64, t = 12)
e: 1, t: 11, age

Excessive output truncated after 524330 bytes.

e: 1, t: 23, agent 7, result: (s = 30, a = :left, r = -1, sp = 29, t = 23)
e: 1, t: 22, agent 8, result: (s = 31, a = :left, r = -1, sp = 30, t = 22)
e: 1, t: 21, agent 9, result: (s = 32, a = :left, r = -1, sp = 31, t = 21)
e: 1, t: 20, agent 10, result: (s = 33, a = :left, r = -1, sp = 32, t = 20)
e: 1, t: 19, agent 11, result: (s = 34, a = :left, r = -1, sp = 33, t = 19)
e: 1, t: 18, agent 12, result: (s = 35, a = :left, r = -1, sp = 34, t = 18)
e: 1, t: 17, agent 13, result: (s = 68, a = :right, r = -1, sp = 69, t = 17)
e: 1, t: 16, agent 14, result: (s = 37, a = :left, r = -1, sp = 36, t = 16)
e: 1, t: 15, agent 15, result: (s = 66, a = :right, r = -1, sp = 67, t = 15)
e: 1, t: 14, agent 16, result: (s = 65, a = :right, r = -1, sp = 66, t = 14)
e: 1, t: 13, agent 17, result: (s = 64, a = :right, r = -1, sp = 65, t = 13)
e: 1, t: 12, agent 18, result: (s = 63, a = :right, r = -1, sp = 64, t = 12)
e: 1, t: 11, agent 19, result: (s = 42, a = :left, r = -1, sp = 41, t = 11)
e: 1, t: 1

12560×6 DataFrame
│ Row   │ run   │ epoch │ agent │ time  │ state │ reward │
│       │ Int64 │ Int64 │ Int64 │ Int64 │ Int64 │ Int64  │
├───────┼───────┼───────┼───────┼───────┼───────┼────────┤
│ 1     │ 1     │ 1     │ 1     │ 1     │ 52    │ -1     │
│ 2     │ 1     │ 1     │ 1     │ 2     │ 51    │ -1     │
│ 3     │ 1     │ 1     │ 2     │ 1     │ 52    │ -1     │
│ 4     │ 1     │ 1     │ 1     │ 3     │ 50    │ -1     │
│ 5     │ 1     │ 1     │ 2     │ 2     │ 53    │ -1     │
│ 6     │ 1     │ 1     │ 3     │ 1     │ 52    │ -1     │
│ 7     │ 1     │ 1     │ 1     │ 4     │ 49    │ -1     │
│ 8     │ 1     │ 1     │ 2     │ 3     │ 54    │ -1     │
│ 9     │ 1     │ 1     │ 3     │ 2     │ 51    │ -1     │
│ 10    │ 1     │ 1     │ 4     │ 1     │ 52    │ -1     │
⋮
│ 12550 │ 10    │ 1     │ 40    │ 10    │ 61    │ -1     │
│ 12551 │ 10    │ 1     │ 41    │ 9     │ 44    │ -1     │
│ 12552 │ 10    │ 1     │ 42    │ 8     │ 45    │ -1     │
│ 12553 │ 10    │ 1     │ 43    │ 7     │ 46    │ -1     │
│ 12554 │ 10    │ 1     │ 44    │ 6     │ 47    │ -1     │
│ 12555 │ 10    │ 1     │ 45    │ 5     │ 48    │ -1     │
│ 12556 │ 10    │ 1     │ 46    │ 4     │ 49    │ -1     │
│ 12557 │ 10    │ 1     │ 47    │ 3     │ 54    │ -1     │
│ 12558 │ 10    │ 1     │ 48    │ 2     │ 51    │ -1     │
│ 12559 │ 10    │ 1     │ 49    │ 1     │ 52    │ -1     │
│ 12560 │ 10    │ 1     │ 1     │ 50    │ 101   │ -10    │

In [72]:
results[(length(results)-10):(length(results)-1)]

10-element Array{Any,1}:
 (10, 1, 40, 10, 61, -1)
 (10, 1, 41, 9, 44, -1) 
 (10, 1, 42, 8, 45, -1) 
 (10, 1, 43, 7, 46, -1) 
 (10, 1, 44, 6, 47, -1) 
 (10, 1, 45, 5, 48, -1) 
 (10, 1, 46, 4, 49, -1) 
 (10, 1, 47, 3, 54, -1) 
 (10, 1, 48, 2, 51, -1) 
 (10, 1, 49, 1, 52, -1) 

In [73]:
length(results)

12560

In [74]:

get_average_regret(df, num_agents)





496×4 DataFrame
│ Row │ run   │ epoch │ agent │ Regret  │
│     │ Int64 │ Int64 │ Int64 │ Float64 │
├─────┼───────┼───────┼───────┼─────────┤
│ 1   │ 1     │ 1     │ 1     │ 116.0   │
│ 2   │ 1     │ 1     │ 2     │ 124.0   │
│ 3   │ 1     │ 1     │ 3     │ 123.0   │
│ 4   │ 1     │ 1     │ 4     │ 122.0   │
│ 5   │ 1     │ 1     │ 5     │ 121.0   │
│ 6   │ 1     │ 1     │ 6     │ 120.0   │
│ 7   │ 1     │ 1     │ 7     │ 119.0   │
│ 8   │ 1     │ 1     │ 8     │ 118.0   │
│ 9   │ 1     │ 1     │ 9     │ 117.0   │
│ 10  │ 1     │ 1     │ 10    │ 116.0   │
│ 11  │ 1     │ 1     │ 11    │ 115.0   │
│ 12  │ 1     │ 1     │ 12    │ 114.0   │
│ 13  │ 1     │ 1     │ 13    │ 113.0   │
│ 14  │ 1     │ 1     │ 14    │ 112.0   │
│ 15  │ 1     │ 1     │ 15    │ 111.0   │
│ 16  │ 1     │ 1     │ 16    │ 110.0   │
│ 17  │ 1     │ 1     │ 17    │ 109.0   │
│ 18  │ 1     │ 1     │ 18    │ 108.0   │
│ 19  │ 1     │ 1     │ 19    │ 107.0   │
│ 20  │ 1     │ 1     │ 20    │ 106.0   │
│ 21  │ 1     │ 1 

│ 224 │ 5     │ 1     │ 25    │ 100.0   │
│ 225 │ 5     │ 1     │ 26    │ 99.0    │
│ 226 │ 5     │ 1     │ 27    │ 98.0    │
│ 227 │ 5     │ 1     │ 28    │ 97.0    │
│ 228 │ 5     │ 1     │ 29    │ 96.0    │
│ 229 │ 5     │ 1     │ 30    │ 95.0    │
│ 230 │ 5     │ 1     │ 31    │ 94.0    │
│ 231 │ 5     │ 1     │ 32    │ 93.0    │
│ 232 │ 5     │ 1     │ 33    │ 92.0    │
│ 233 │ 5     │ 1     │ 34    │ 91.0    │
│ 234 │ 5     │ 1     │ 35    │ 90.0    │
│ 235 │ 5     │ 1     │ 36    │ 89.0    │
│ 236 │ 5     │ 1     │ 37    │ 88.0    │
│ 237 │ 5     │ 1     │ 38    │ 87.0    │
│ 238 │ 5     │ 1     │ 39    │ 86.0    │
│ 239 │ 5     │ 1     │ 40    │ 85.0    │
│ 240 │ 5     │ 1     │ 41    │ 84.0    │
│ 241 │ 5     │ 1     │ 42    │ 83.0    │
│ 242 │ 5     │ 1     │ 43    │ 82.0    │
│ 243 │ 5     │ 1     │ 44    │ 81.0    │
│ 244 │ 5     │ 1     │ 45    │ 80.0    │
│ 245 │ 5     │ 1     │ 46    │ 79.0    │
│ 246 │ 5     │ 1     │ 47    │ 78.0    │
│ 247 │ 5     │ 1     │ 48    │ 77

│ 433 │ 9     │ 1     │ 36    │ 90.0    │
│ 434 │ 9     │ 1     │ 37    │ 89.0    │
│ 435 │ 9     │ 1     │ 38    │ 88.0    │
│ 436 │ 9     │ 1     │ 39    │ 87.0    │
│ 437 │ 9     │ 1     │ 40    │ 86.0    │
│ 438 │ 9     │ 1     │ 41    │ 85.0    │
│ 439 │ 9     │ 1     │ 42    │ 84.0    │
│ 440 │ 9     │ 1     │ 43    │ 83.0    │
│ 441 │ 9     │ 1     │ 44    │ 82.0    │
│ 442 │ 9     │ 1     │ 45    │ 81.0    │
│ 443 │ 9     │ 1     │ 46    │ 80.0    │
│ 444 │ 9     │ 1     │ 47    │ 79.0    │
│ 445 │ 9     │ 1     │ 48    │ 78.0    │
│ 446 │ 9     │ 1     │ 49    │ 77.0    │
│ 447 │ 9     │ 1     │ 50    │ 76.0    │
│ 448 │ 10    │ 1     │ 1     │ 134.0   │
│ 449 │ 10    │ 1     │ 2     │ 123.0   │
│ 450 │ 10    │ 1     │ 3     │ 122.0   │
│ 451 │ 10    │ 1     │ 4     │ 121.0   │
│ 452 │ 10    │ 1     │ 5     │ 120.0   │
│ 453 │ 10    │ 1     │ 6     │ 119.0   │
│ 454 │ 10    │ 1     │ 7     │ 118.0   │
│ 455 │ 10    │ 1     │ 8     │ 117.0   │
│ 456 │ 10    │ 1     │ 9     │ 11

Agent 408 not in regret
Agent 409 not in regret
Agent 410 not in regret
Agent 411 not in regret
Agent 412 not in regret
Agent 413 not in regret
Agent 414 not in regret
Agent 415 not in regret
Agent 416 not in regret
Agent 417 not in regret
Agent 418 not in regret
Agent 419 not in regret
Agent 420 not in regret
Agent 421 not in regret
Agent 422 not in regret
Agent 423 not in regret
Agent 424 not in regret
Agent 425 not in regret
Agent 426 not in regret
Agent 427 not in regret
Agent 428 not in regret
Agent 429 not in regret
Agent 430 not in regret
Agent 431 not in regret
Agent 432 not in regret
Agent 433 not in regret
Agent 434 not in regret
Agent 435 not in regret
Agent 436 not in regret
Agent 437 not in regret
Agent 438 not in regret
Agent 439 not in regret
Agent 440 not in regret
Agent 441 not in regret
Agent 442 not in regret
Agent 443 not in regret
Agent 444 not in regret
Agent 445 not in regret
Agent 446 not in regret
Agent 447 not in regret
Agent 448 not in regret
Agent 449 not in

Agent 871 not in regret
Agent 872 not in regret
Agent 873 not in regret
Agent 874 not in regret
Agent 875 not in regret
Agent 876 not in regret
Agent 877 not in regret
Agent 878 not in regret
Agent 879 not in regret
Agent 880 not in regret
Agent 881 not in regret
Agent 882 not in regret
Agent 883 not in regret
Agent 884 not in regret
Agent 885 not in regret
Agent 886 not in regret
Agent 887 not in regret
Agent 888 not in regret
Agent 889 not in regret
Agent 890 not in regret
Agent 891 not in regret
Agent 892 not in regret
Agent 893 not in regret
Agent 894 not in regret
Agent 895 not in regret
Agent 896 not in regret
Agent 897 not in regret
Agent 898 not in regret
Agent 899 not in regret
Agent 900 not in regret
Agent 901 not in regret
Agent 902 not in regret
Agent 903 not in regret
Agent 904 not in regret
Agent 905 not in regret
Agent 906 not in regret
Agent 907 not in regret
Agent 908 not in regret
Agent 909 not in regret
Agent 910 not in regret
Agent 911 not in regret
Agent 912 not in

...

│ 3932  │ 6     │ 1     │ 394   │ 0.0     │
│ 3933  │ 7     │ 1     │ 394   │ 0.0     │
│ 3934  │ 8     │ 1     │ 394   │ 0.0     │
│ 3935  │ 9     │ 1     │ 394   │ 0.0     │
│ 3936  │ 10    │ 1     │ 394   │ 0.0     │
│ 3937  │ 1     │ 1     │ 395   │ 0.0     │
│ 3938  │ 2     │ 1     │ 395   │ 0.0     │
│ 3939  │ 3     │ 1     │ 395   │ 0.0     │
│ 3940  │ 4     │ 1     │ 395   │ 0.0     │
│ 3941  │ 5     │ 1     │ 395   │ 0.0     │
│ 3942  │ 6     │ 1     │ 395   │ 0.0     │
│ 3943  │ 7     │ 1     │ 395   │ 0.0     │
│ 3944  │ 8     │ 1     │ 395   │ 0.0     │
│ 3945  │ 9     │ 1     │ 395   │ 0.0     │
│ 3946  │ 10    │ 1     │ 395   │ 0.0     │
│ 3947  │ 1     │ 1     │ 396   │ 0.0     │
│ 3948  │ 2     │ 1     │ 396   │ 0.0     │
│ 3949  │ 3     │ 1     │ 396   │ 0.0     │
│ 3950  │ 4     │ 1     │ 396   │ 0.0     │
│ 3951  │ 5     │ 1     │ 396   │ 0.0     │
│ 3952  │ 6     │ 1     │ 396   │ 0.0     │
│ 3953  │ 7     │ 1     │ 396   │ 0.0     │
│ 3954  │ 8     │ 1     │ 396   

│ 4208  │ 2     │ 1     │ 422   │ 0.0     │
│ 4209  │ 3     │ 1     │ 422   │ 0.0     │
│ 4210  │ 4     │ 1     │ 422   │ 0.0     │
│ 4211  │ 5     │ 1     │ 422   │ 0.0     │
│ 4212  │ 6     │ 1     │ 422   │ 0.0     │
│ 4213  │ 7     │ 1     │ 422   │ 0.0     │
│ 4214  │ 8     │ 1     │ 422   │ 0.0     │
│ 4215  │ 9     │ 1     │ 422   │ 0.0     │
│ 4216  │ 10    │ 1     │ 422   │ 0.0     │
│ 4217  │ 1     │ 1     │ 423   │ 0.0     │
│ 4218  │ 2     │ 1     │ 423   │ 0.0     │
│ 4219  │ 3     │ 1     │ 423   │ 0.0     │
│ 4220  │ 4     │ 1     │ 423   │ 0.0     │
│ 4221  │ 5     │ 1     │ 423   │ 0.0     │
│ 4222  │ 6     │ 1     │ 423   │ 0.0     │
│ 4223  │ 7     │ 1     │ 423   │ 0.0     │
│ 4224  │ 8     │ 1     │ 423   │ 0.0     │
│ 4225  │ 9     │ 1     │ 423   │ 0.0     │
│ 4226  │ 10    │ 1     │ 423   │ 0.0     │
│ 4227  │ 1     │ 1     │ 424   │ 0.0     │
│ 4228  │ 2     │ 1     │ 424   │ 0.0     │
│ 4229  │ 3     │ 1     │ 424   │ 0.0     │
│ 4230  │ 4     │ 1     │ 424   

Excessive output truncated after 524289 bytes.

0.0     │
│ 4392  │ 6     │ 1     │ 440   │ 0.0     │
│ 4393  │ 7     │ 1     │ 440   │ 0.0     │
│ 4394  │ 8     │ 1     │ 440   │ 0.0     │
│ 4395  │ 9     │ 1     │ 440   │ 0.0     │
│ 4396  │ 10    │ 1     │ 440   │ 0.0     │
│ 4397  │ 1     │ 1     │ 441   │ 0.0     │
│ 4398  │ 2     │ 1     │ 441   │ 0.0     │
│ 4399  │ 3     │ 1     │ 441   │ 0.0     │
│ 4400  │ 4     │ 1     │ 441   │ 0.0     │
│ 4401  │ 5     │ 1     │ 441   │ 0.0     │
│ 4402  │ 6     │ 1     │ 441   │ 0.0     │
│ 4403  │ 7     │ 1     │ 441   │ 0.0     │
│ 4404  │ 8     │ 1     │ 441   │ 0.0     │
│ 4405  │ 9     │ 1     │ 441   │ 0.0     │
│ 4406  │ 10    │ 1     │ 441   │ 0.0     │
│ 4407  │ 1     │ 1     │ 442   │ 0.0     │
│ 4408  │ 2     │ 1     │ 442   │ 0.0     │
│ 4409  │ 3     │ 1     │ 442   │ 0.0     │
│ 4410  │ 4     │ 1     │ 442   │ 0.0     │
│ 4411  │ 5     │ 1     │ 442   │ 0.0     │
│ 4412  │ 6     │ 1     │ 442   │ 0.0     │
│ 4413  │ 7     │ 1     │ 442   │ 0.0     │
│ 4414  │ 8     │ 1   

0.49737989519580783

In [44]:

num_states
R = (num_states - 2) / 2
max_theta_state = 2
for ag in 1:num_agents
    max_s = by(df, [:epoch, :agent], :state => maximum)
    print("$ag max: $max_s")
end

1 max: 10×3 DataFrame
│ Row │ epoch │ agent │ state_maximum │
│     │ Int64 │ Int64 │ Int64         │
├─────┼───────┼───────┼───────────────┤
│ 1   │ 1     │ 1     │ 101           │
│ 2   │ 1     │ 2     │ 100           │
│ 3   │ 1     │ 3     │ 99            │
│ 4   │ 1     │ 4     │ 98            │
│ 5   │ 1     │ 5     │ 97            │
│ 6   │ 1     │ 6     │ 96            │
│ 7   │ 1     │ 7     │ 95            │
│ 8   │ 1     │ 8     │ 94            │
│ 9   │ 1     │ 9     │ 93            │
│ 10  │ 1     │ 10    │ 92            │2 max: 10×3 DataFrame
│ Row │ epoch │ agent │ state_maximum │
│     │ Int64 │ Int64 │ Int64         │
├─────┼───────┼───────┼───────────────┤
│ 1   │ 1     │ 1     │ 101           │
│ 2   │ 1     │ 2     │ 100           │
│ 3   │ 1     │ 3     │ 99            │
│ 4   │ 1     │ 4     │ 98            │
│ 5   │ 1     │ 5     │ 97            │
│ 6   │ 1     │ 6     │ 96            │
│ 7   │ 1     │ 7     │ 95            │
│ 8   │ 1     │ 8     │ 94           